In [191]:
import sys, os
module_path = os.path.abspath(os.path.join('..'))
module_path = os.path.join(module_path, 'scripts')
if module_path not in sys.path:
    sys.path.append(module_path)

In [192]:
import pprint
import pandas as pd
import uuid
import json
import os
import glob
import re
import sys
from bs4 import NavigableString, BeautifulSoup
from collections import defaultdict
import random
import string

from utils.config import config
from utils.logger.logger import loggerCreator

## ePI Modules
from parse.rulebook.rulebook import StyleRulesDictionary

from parse.extractor.parser import parserExtractor
from match.matchDocument.matchDocument import MatchDocument
from documentAnnotation.documentAnnotation import DocumentAnnotation
from htmlDocTypePartitioner.partition import DocTypePartitioner
from extractContentBetweenHeadings.dataBetweenHeadingsExtractor import DataBetweenHeadingsExtractor
from fhirXmlGenerator.fhirXmlGenerator import FhirXmlGenerator

%load_ext autoreload

%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [89]:
def getRandomString(N):
    str_ = ''.join(random.choice(string.ascii_uppercase + string.digits \
            + string.ascii_lowercase) for _ in range(N))
    return str_



# Set Required Field for Parsing and Partition Modules

### Please ensure that your converted_html folder has html files in their specific language folders

Example: If your language code is en, please ensure that all html files reside in the converted_html/en folder. If folder is not present, a folder not found exception will be thrown

### English

In [319]:
ePILanguage = 'en'
fileNameQrd = 'qrd_canonical_mode_CAP_NAP.csv'
procedureType = 'CAP'

### German

In [264]:
ePILanguage = 'de'
fileNameQrd = 'qrd_canonical_mode_CAP_NAP.csv'
procedureType = 'CAP'

### Spanish

In [65]:
ePILanguage = 'es'
fileNameQrd = 'qrd_canonical_mode_CAP_NAP.csv'
procedureType = 'CAP'

# Html Parsing Stage

In [320]:
class FolderNotFoundError(Exception):
    pass

## Generate input folder path
module_path = os.path.abspath(os.path.join('..'))
module_path = os.path.join(module_path, 'data')
module_path = os.path.join(module_path, 'converted_to_html')
module_path = os.path.join(module_path, ePILanguage)

## Generate output folder path
output_json_path = module_path.replace('converted_to_html','outputJSON')

"""
    Check if input folder exists, else throw exception
"""
if(os.path.exists(module_path)):
    filenames = glob.glob(os.path.join(module_path, '*.html'))
    filenames.extend(glob.glob(os.path.join(module_path, '*.htm')))
    
    ## Create language specific folder in outputJSON folder if it doesn't exist
    if(not os.path.exists(output_json_path)):
        os.mkdir(output_json_path)
    logger = loggerCreator('Parser_'+ getRandomString(1))
    
    styleRulesObj = StyleRulesDictionary(loggerCreator('Style Dictionary_'+ getRandomString(1)),
                                     language = ePILanguage,
                                     fileName = fileNameQrd,
                                     procedureType = procedureType)

    parserObj = parserExtractor(config, logger, styleRulesObj.styleRuleDict, 
                            styleRulesObj.styleFeatureKeyList, 
                            styleRulesObj.qrd_section_headings)

    for input_filename in filenames:
      if(input_filename.find('Kalydeco II-86-PI-clean')!=-1):
        output_filename = input_filename.replace('converted_to_html','outputJSON')
        output_filename = output_filename.replace('.html','.json')
        output_filename = output_filename.replace('.htm','.json')
        print(input_filename, output_filename)
        parserObj.createPIJsonFromHTML(input_filepath = input_filename,
                                       output_filepath = output_filename,
                                       img_base64_dict= parserObj.convertImgToBase64(input_filename),
                                      )
else:
    raise FolderNotFoundError(module_path + " not found")

2021-04-26 02:18:12,611 : Style Dictionary_6 : Creating default style dictionary in file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\styleRules\rule_dictionary_en.json
2021-04-26 02:18:12,690 : Style Dictionary_6 : Qrd Section Keys Generated: ANNEX I, ANNEX II, ANNEX III, B. PACKAGE LEAFLET


F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\converted_to_html\en\Kalydeco II-86-PI-clean.html F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\outputJSON\en\Kalydeco II-86-PI-clean.json


2021-04-26 02:18:21,938 : Parser_D : Writing to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\outputJSON\en\Kalydeco II-86-PI-clean.json


# Partition Stage

In [321]:
styleRulesObj = StyleRulesDictionary(loggerCreator('Style Dictionary_'+ getRandomString(1)), 
                                     language = ePILanguage,
                                     fileName = fileNameQrd,
                                     procedureType = procedureType)

path_json = os.path.join(os.path.abspath(os.path.join('..')), 'data', 'outputJSON', ePILanguage)

partitionlogger = loggerCreator('Partition_'+ getRandomString(1))
partitioner = DocTypePartitioner(partitionlogger)
partitioner.partitionHtmls(styleRulesObj.qrd_section_headings, path_json)

2021-04-26 02:18:36,050 : Style Dictionary_R : Reading style dictionary in file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\styleRules\rule_dictionary_en.json
2021-04-26 02:18:36,050 : Style Dictionary_R : Reading style dictionary in file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\styleRules\rule_dictionary_en.json
2021-04-26 02:18:36,103 : Style Dictionary_R : Qrd Section Keys Generated: ANNEX I, ANNEX II, ANNEX III, B. PACKAGE LEAFLET
2021-04-26 02:18:36,103 : Style Dictionary_R : Qrd Section Keys Generated: ANNEX I, ANNEX II, ANNEX III, B. PACKAGE LEAFLET
2021-04-26 02:18:36,118 : Partition_8 : Partitioning Json: Kalydeco II-86-PI-clean.json


*************************** Texts with more than 2 characters**************************************


Bold           Classes  \
0   False  ['WordSection1']   
24   True     ['MsoNormal']   
26   True        ['TitleA']   
32   True              None   
34  False     ['MsoNormal']   

                                                                                                                                                                                                    Element  \
0   <div class="WordSection1"> <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><b><span lang="EN-GB"> </span></b></p> <p align="center" class="MsoNormal" style="text-a...   
24                                                                            <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><b><span lang="EN-GB">ANNEX I</span></b></p>   
26                                                                                                                       <p class="TitleA"><span lang="EN-GB">SUMMARY OF PRODUCT CHARACTERISTICS</span></p>   
32                                               <h1 style="margin:0in"><span lang="EN-GB" style='font-size:11.0pt;font-family: "Times New Roman",serif'>1.       NAME OF THE MEDICINAL PRODUCT</span></h1>   
34                                                                 <p class="MsoNormal" style="line-height:normal;page-break-after:avoid"><span lang="EN-GB">Kalydeco 150 mg film‑coated tablets</span></p>   

    HasBorder                                    ID  Indexed IsHeadingType  \
0       False  73096ebe-2c3d-436c-a95e-1603e3dc2f47    False          None   
24      False  e0889eaf-03a1-499e-8359-cbe3b2729087    False          None   
26      False  73c60cce-cadb-41b3-8bb9-8ccf958d972a    False          None   
32      False  f20bd308-1923-4f21-8683-66eb29755c2e     True            L1   
34      False  e84da6e3-d451-4d51-b713-487421166004    False          None   

    IsListItem  IsPossibleHeading  Italics  \
0        False              False    False   
24       False               True    False   
26       False              False    False   
32       False               True    False   
34       False              False    False   

                                ParentId  \
0   4c9313d0-78ec-468f-ba9c-707d28cf9f41   
24  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
26  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
32  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
34  73096ebe-2c3d-436c-a95e-1603e3dc2f47   

                                       Styles  \
0                                        None   
24       text-align:center;line-height:normal   
26                                       None   
32                                 margin:0in   
34  line-height:normal;page-break-after:avoid   

                                                                                                                                                                                                       Text  \
0                                                                                                                                                                                                       ...   
24                                                                                                                                                                                                  ANNEX I   
26                                                                                                                                                                       SUMMARY OF PRODUCT CHARACTERISTICS   
32                                                                                                                                                                   1.       NAME OF THE MEDICINAL PRODUCT   
34                                                                                                                                                                      Kalydeco 150 mg film‑coated tablets   

    Underlined  Uppercased

2021-04-26 02:18:36,408 : Partition_8 : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_SmPC.json


*************************** Texts with more than 2 characters**************************************


...

Bold        Classes  \
1304   True  ['MsoNormal']   
1306   True  ['MsoNormal']   
1345   True     ['TitleA']   
1349  False           None   
1350   True  ['MsoNormal']   

                                                                                                                                                                                                      Element  \
1304                                                                          <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><b><span lang="EN-GB">ANNEX III</span></b></p>   
1306                                                      <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><b><span lang="EN-GB">LABELLING AND PACKAGE LEAFLET</span></b></p>   
1345                                                                                                                                             <p class="TitleA"><span lang="EN-GB">A. LABELLING</span></p>   
1349  <div style="border:solid windowtext 1.0pt;padding:1.0pt 4.0pt 1.0pt 4.0pt"> <p class="MsoNormal" style="margin-left:28.35pt;text-indent:-28.35pt;line-height: normal;border:none;padding:0in"><b><sp...   
1350      <p class="MsoNormal" style="margin-left:28.35pt;text-indent:-28.35pt;line-height: normal;border:none;padding:0in"><b><span lang="EN-GB">PARTICULARS TO APPEAR ON THE OUTER PACKAGING</span></b></p>   

      HasBorder                                    ID  Indexed IsHeadingType  \
1304      False  0b0ad730-65b9-403e-835e-2dc64e093e9d    False            L1   
1306      False  0a5d42a1-5f0c-46d0-a579-20dae3dd6be7    False            L1   
1345      False  d3dc3b68-fa13-4e32-888e-68f5482bacc0     True            L2   
1349       True  95505895-0d47-44b6-9965-79992f2c4342    False          None   
1350      False  6561322c-ce30-4c5f-abb7-c190b4f2f183    False            L1   

      IsListItem  IsPossibleHeading  Italics  \
1304       False               True    False   
1306       False               True    False   
1345       False               True    False   
1349       False              False    False   
1350       False               True    False   

                                  ParentId  \
1304  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
1306  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
1345  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
1349  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
1350  95505895-0d47-44b6-9965-79992f2c4342   

                                                                                     Styles  \
1304                                                   text-align:center;line-height:normal   
1306                                                   text-align:center;line-height:normal   
1345                                                                                   None   
1349                          border:solid windowtext 1.0pt;padding:1.0pt 4.0pt 1.0pt 4.0pt   
1350  margin-left:28.35pt;text-indent:-28.35pt;line-height:\nnormal;border:none;padding:0in   

                                              Text  Underlined  Uppercased  
1304                                     ANNEX III       False        True  
1306                 LABELLING AND PACKAGE LEAFLET       False        True  
1345                                  A. LABELLING       False        True  
1349                                                     False       False  
1350  PARTICULARS TO APPEAR ON THE OUTER PACKAGING       False        True

2021-04-26 02:18:36,903 : Partition_8 : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_ANNEX III.json


*************************** Texts with more than 2 characters**************************************


Bold        Classes  \
2918   True     ['TitleA']   
2923   True  ['MsoNormal']   
2925   True  ['MsoNormal']   
2926  False  ['MsoNormal']   
2929   True  ['MsoNormal']   

                                                                                                                                                                                                      Element  \
2918                                                                                                                                       <p class="TitleA"><span lang="EN-GB">B. PACKAGE LEAFLET</span></p>   
2923                                       <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><b><span lang="EN-GB">Package leaflet: Information for the patient</span></b></p>   
2925                                                <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><b><span lang="EN-GB">Kalydeco 150 mg film-coated tablets</span></b></p>   
2926                                                                                 <p align="center" class="MsoNormal" style="text-align:center;line-height:normal"><span lang="EN-GB">ivacaftor</span></p>   
2929  <p class="MsoNormal" style="line-height:normal;page-break-after:avoid"><b><span lang="EN-GB">Read all of this leaflet carefully before you start taking this medicine because it contains important ...   

      HasBorder                                    ID  Indexed IsHeadingType  \
2918      False  2e155332-ec5e-4fcd-9322-ad35c12af6d6     True          None   
2923      False  448aaebe-f42a-45f6-9147-3edac730cbe1    False            L2   
2925      False  787c1333-bd90-4c2e-aaf4-d90bd6a94fce    False            L2   
2926      False  9db5d5f0-94f1-4705-b5c0-43a2980ecf94    False          None   
2929      False  766e009f-786b-48e9-8a13-e668acadec36    False            L2   

      IsListItem  IsPossibleHeading  Italics  \
2918       False               True    False   
2923       False               True    False   
2925       False               True    False   
2926       False              False    False   
2929       False               True    False   

                                  ParentId  \
2918  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
2923  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
2925  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
2926  73096ebe-2c3d-436c-a95e-1603e3dc2f47   
2929  73096ebe-2c3d-436c-a95e-1603e3dc2f47   

                                         Styles  \
2918                                       None   
2923       text-align:center;line-height:normal   
2925       text-align:center;line-height:normal   
2926       text-align:center;line-height:normal   
2929  line-height:normal;page-break-after:avoid   

                                                                                                                             Text  \
2918                                                                                                           B. PACKAGE LEAFLET   
2923                                                                                 Package leaflet: Information for the patient   
2925                                                                                          Kalydeco 150 mg film-coated tablets   
2926                                                                                                                    ivacaftor   
2929  Read all of this leaflet carefully before you start taking this medicine because it contains important information for you.   

      Underlined  Uppercased  
2918       False        True  
2923       False       False  
2925       False       False  
2926       False       False  
2929       False       False

2021-04-26 02:18:37,038 : Partition_8 : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json


# Matching Stage

In [100]:
procedureType = 'CAP'
languageCode = 'es'
stopWordlanguage = 'spanish'
fileNameQrd = 'qrd_canonical_mode_CAP_NAP.csv'
fileNameMatchRuleBook = 'ruleDict.json'
fileNameDocumentTypeNames = 'documentTypeNames.json'

In [101]:
### SmPC
documentNumber = 3
docFilter = "PROSPECTO.json"
stopWordFilterLen = 100
start=0
end=1
isPackageLeaflet=True

In [102]:
parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end,
               isPackageLeaflet,
               'Kalydeco'
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es
['emea-combined-h-2494-es_ PROSPECTO.json', 'emea-combined-h-2494-es_ANEXO II.json', 'emea-combined-h-2494-es_ANEXO III.json', 'emea-combined-h-2494-es_SmPC.json']
['emea-combined-h-2494-es_ PROSPECTO.json']
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_ PROSPECTO.json
--------------------------------------------
Package leaflet
True  ||  <=1|25.0|(86, 100, 95)|0.95|  ||  B. PROSPECTO  ||  PROSPECTO
True  ||    ||  Contenido del prospecto  ||  Contenido del prospecto
----------------------------------
RemovedByStyle  ||  >7|2.5|(99, 97, 99)|1.0|  ||  1.    Qué es Kalydeco y para qué se utiliza  ||  1 Qué es Kalydeco y para qué se utiliza
----------------------------------
----------------------------------
RemovedByStyle  ||  Contains<>|16.36|(92, 85, 95)|0.97|  ||  2.    Qué necesita saber antes de empezar a tomar Kalydeco  ||  2 Q


OriginalCheck
('<=7|21.15|(88, 100, 95)|0.98|', 'Si interrumpe el tratamiento con Kalydeco de su hijo', 'Si interrumpe el tratamiento con Kalydeco')

True  ||  <=4|3.57|(98, 96, 98)|0.99|  ||  4.            Posibles efectos adversos  ||  4 Posibles efectos adversos
True  ||  Contains<>|38.46|(78, 75, 88)|0.86|  ||  Efectos adversos adicionales en niños y adolescentes  ||  Otros efectos adversos en niños <y adolescentes>
True  ||    ||  Comunicación de efectos adversos  ||  Comunicación de efectos adversos
True  ||  <=4|3.7|(98, 96, 98)|0.99|  ||  5.            Conservación de Kalydeco  ||  5 Conservación de Kalydeco
True  ||  <=7|2.13|(99, 98, 99)|1.0|  ||  6.            Contenido del envase e información adicional  ||  6 Contenido del envase e información adicional
True  ||    ||  Composición de Kalydeco  ||  Composición de Kalydeco 
True  ||    ||  Aspecto del producto y contenido del envase  ||  Aspecto del producto y contenido del envase
True  ||  Contains<>|73.91|(73, 100, 90)|0.

2021-04-25 22:06:24,367 : ExtractContentBetween_r : Cleaning Match Results
2021-04-25 22:06:24,370 : ExtractContentBetween_r : Finished Cleaning Match Results
2021-04-25 22:06:24,382 : ExtractContentBetween_r : Extracting Content Between Headings
2021-04-25 22:06:24,392 : ExtractContentBetween_r : Finished Extracting Content Between Headings




Heading Not Found 
 ['q Este medicamento está sujeto a seguimiento adicional, lo que agilizará la detección de nueva información sobre su seguridad. Puede contribuir comunicando los efectos adversos que pudiera usted tener. La parte final de la sección 4 incluye información sobre cómo comunicar estos efectos adversos.', 'X contiene {nombre del (de los) excipiente(s)}', 'Pueden solicitar más información respecto a este medicamento dirigiéndose al representante local del titular de la autorización de comercialización:', 'Esta información está destinada únicamente a profesionales sanitarios:']


dict_keys(['1 Qué es Kalydeco y para qué se utiliza', '2 Qué necesita saber antes de empezar a <tomar><usar> Kalydeco', '3 Cómo <tomar><usar> Kalydeco', '4 Posibles efectos adversos', '5 Conservación de Kalydeco', '6 Contenido del envase e información adicional', 'Kalydeco contiene {nombre del (de los) excipiente(s)}'])
Error Found
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\fun

index     id Procedure type Display code  \
0     922  27001            CAP          NaN   
1     924  27003            CAP          NaN   
2     925  27004            CAP            1   
3     926  27005            CAP            2   
4     927  27006            CAP          NaN   
5     928  27007            CAP          NaN   
6     929  27008            CAP          NaN   
7     930  27009            CAP          NaN   
8     931  27010            CAP          NaN   
9     932  27011            CAP          NaN   
10    933  27012            CAP          NaN   
11    935  27014            CAP            3   
12    936  27015            CAP          NaN   
13    937  27016            CAP          NaN   
14    938  27017            CAP          NaN   
15    939  27018            CAP          NaN   
16    940  27019            CAP            4   
17    941  27020            CAP          NaN   
18    942  27021            CAP          NaN   
19    943  27022            CAP            5   
20    944  27023            CAP            6   
21    945  27024            CAP          NaN   
22    946  27025            CAP          NaN   
23    947  27026            CAP          NaN   
24    949  27028            CAP          NaN   
25    950  27029            CAP          NaN   
26    924  27003            CAP          NaN   
27    925  27004            CAP            1   
28    926  27005            CAP            2   
29    927  27006            CAP          NaN   
30    928  27007            CAP          NaN   
31    930  27009            CAP          NaN   
32    931  27010            CAP          NaN   
33    933  27012            CAP          NaN   
34    935  27014            CAP            3   
35    937  27016            CAP          NaN   
36    940  27019            CAP            4   
37    941  27020            CAP          NaN   
38    942  27021            CAP          NaN   
39    943  27022            CAP            5   
40    944  27023            CAP            6   
41    945  27024            CAP          NaN   
42    946  27025            CAP          NaN   
43    947  27026            CAP          NaN   
44    949  27028            CAP          NaN   
45    950  27029            CAP          NaN   

                                                                                Name  \
0                                                                          PROSPECTO   
1                                                            Contenido del prospecto   
2                                                     Qué es X y para qué se utiliza   
3                              Qué necesita saber antes de empezar a <tomar><usar> X   
4                                                                   No <tome><use> X   
5                                                       Advertencias y precauciones    
6                                                             Niños <y adolescentes>   
7                                                             Otros medicamentos y X   
8                        <Uso><Toma> de X con <alimentos><y><,><bebidas><y><alcohol>   
9                                           Embarazo <y><,> lactancia <y fertilidad>   
10                                                      Conducción y uso de máquinas   
11                                                              Cómo <tomar><usar> X   
12                                                     Uso en niños <y adolescentes>   
13                                                 Si <toma><usa> más X del que debe   
14                                                         Si olvidó <tomar><usar> X   
15                                                Si interrumpe el tratamiento con X   
16                                                         Posibles efectos adversos   
17                                  Otros efectos adversos en niños <y adolescentes>   
18                                                  Comunicación de efectos

2021-04-25 22:06:24,436 : XmlGeneration_H : Initiating XML Generation
2021-04-25 22:06:24,547 : XmlGeneration_H : Writing to File:emea-combined-h-2494-es_ PROSPECTO.xml


# Content Extraction Stage

In [83]:
extractContentlogger = loggerCreator('ExtractContentBetween_'+ getRandomString(1))
extractorObj = DataBetweenHeadingsExtractor(extractContentlogger, coll)
dfExtractedHierRR = extractorObj.extractContentBetweenHeadings('Abilify-h-471-e_ PACKAGE LEAFLET.json')

2021-04-22 11:47:46,065 : ExtractContentBetween_y : Cleaning Match Results
2021-04-22 11:47:46,070 : ExtractContentBetween_y : Finished Cleaning Match Results
2021-04-22 11:47:46,098 : ExtractContentBetween_y : Extracting Content Between Headings
2021-04-22 11:47:46,121 : ExtractContentBetween_y : Finished Extracting Content Between Headings


File being processed: C:\Users\psaga\source\repos\EMA\EMA%20EPI%20PoC\function_code\data\partitionedJSONs\Abilify-h-471-e_ PACKAGE LEAFLET.json
--------------------------------------------


index     id Procedure type Display code  \
0      786  23001            CAP          NaN   
1      788  23003            CAP          NaN   
2      789  23004            CAP            1   
3      790  23005            CAP            2   
4      791  23006            CAP          NaN   
5      792  23007            CAP          NaN   
6      793  23008            CAP          NaN   
7      794  23009            CAP          NaN   
8      795  23010            CAP          NaN   
9      796  23011            CAP          NaN   
10     797  23012            CAP          NaN   
11     798  23013            CAP          NaN   
12     799  23014            CAP            3   
13     800  23015            CAP          NaN   
14     801  23016            CAP          NaN   
15     802  23017            CAP          NaN   
16     803  23018            CAP          NaN   
17     804  23019            CAP            4   
18     805  23020            CAP          NaN   
19     806  23021            CAP          NaN   
20     807  23022            CAP            5   
21     808  23023            CAP            6   
22     809  23024            CAP          NaN   
23     810  23025            CAP          NaN   
24     811  23026            CAP          NaN   
25     813  23028            CAP          NaN   
26     814  23029            CAP          NaN   
27     788  23003            CAP          NaN   
28     789  23004            CAP            1   
29     790  23005            CAP            2   
30     791  23006            CAP          NaN   
31     792  23007            CAP          NaN   
32     793  23008            CAP          NaN   
33     794  23009            CAP          NaN   
34     795  23010            CAP          NaN   
35     796  23011            CAP          NaN   
36     797  23012            CAP          NaN   
37     798  23013            CAP          NaN   
38     798  23013            CAP          NaN   
39     798  23013            CAP          NaN   
40     799  23014            CAP            3   
41     800  23015            CAP          NaN   
42     801  23016            CAP          NaN   
43     802  23017            CAP          NaN   
44     803  23018            CAP          NaN   
45     804  23019            CAP            4   
46     805  23020            CAP          NaN   
47     806  23021            CAP          NaN   
48     807  23022            CAP            5   
49     808  23023            CAP            6   
50     809  23024            CAP          NaN   
51     810  23025            CAP          NaN   
52     811  23026            CAP          NaN   
53     813  23028            CAP          NaN   
54     814  23029            CAP          NaN   
55     788  23003            CAP          NaN   
56     789  23004            CAP            1   
57     790  23005            CAP            2   
58     791  23006            CAP          NaN   
59     792  23007            CAP          NaN   
60     793  23008            CAP          NaN   
61     794  23009            CAP          NaN   
62     795  23010            CAP          NaN   
63     796  23011            CAP          NaN   
64     797  23012            CAP          NaN   
65     798  23013            CAP          NaN   
66     798  23013            CAP          NaN   
67     798  23013            CAP          NaN   
68     799  23014            CAP            3   
69     800  23015            CAP          NaN   
70     801  23016            CAP          NaN   
71     802  23017            CAP          NaN   
72     803  23018            CAP          NaN   
73     804  23019            CAP            4   
74     805  23020            CAP          NaN   
75     806  23021            CAP          NaN   
76     807  23022            CAP            5   
77     808  23023            CAP            6   
78     809  23024            CAP          NaN   
79     810  23025            CAP          NaN   
80     811  23026            CAP    

# XML Generation Stage

In [84]:
xmlLogger = loggerCreator('XmlGeneration_'+ getRandomString(1))
fhirXmlGeneratorObj = FhirXmlGenerator(xmlLogger)
fhirXmlGeneratorObj.generateXml(dfExtractedHierRR,  'Abilify-h-471-e_ PACKAGE LEAFLET.xml')

2021-04-22 11:47:56,146 : XmlGeneration_4 : Initiating XML Generation
2021-04-22 11:47:56,415 : XmlGeneration_4 : Writing to File:Abilify-h-471-e_ PACKAGE LEAFLET.xml


In [75]:
convertCollectionToDataFrame(coll)

index     id Procedure type Display code  \
0      786  23001            CAP          NaN   
1      788  23003            CAP          NaN   
2      789  23004            CAP            1   
3      790  23005            CAP            2   
4      791  23006            CAP          NaN   
5      792  23007            CAP          NaN   
6      793  23008            CAP          NaN   
7      794  23009            CAP          NaN   
8      795  23010            CAP          NaN   
9      796  23011            CAP          NaN   
10     797  23012            CAP          NaN   
11     798  23013            CAP          NaN   
12     799  23014            CAP            3   
13     800  23015            CAP          NaN   
14     801  23016            CAP          NaN   
15     802  23017            CAP          NaN   
16     803  23018            CAP          NaN   
17     804  23019            CAP            4   
18     805  23020            CAP          NaN   
19     806  23021            CAP          NaN   
20     807  23022            CAP            5   
21     808  23023            CAP            6   
22     809  23024            CAP          NaN   
23     810  23025            CAP          NaN   
24     811  23026            CAP          NaN   
25     813  23028            CAP          NaN   
26     814  23029            CAP          NaN   
27     788  23003            CAP          NaN   
28     789  23004            CAP            1   
29     790  23005            CAP            2   
30     791  23006            CAP          NaN   
31     792  23007            CAP          NaN   
32     793  23008            CAP          NaN   
33     794  23009            CAP          NaN   
34     795  23010            CAP          NaN   
35     796  23011            CAP          NaN   
36     797  23012            CAP          NaN   
37     798  23013            CAP          NaN   
38     798  23013            CAP          NaN   
39     798  23013            CAP          NaN   
40     799  23014            CAP            3   
41     800  23015            CAP          NaN   
42     801  23016            CAP          NaN   
43     802  23017            CAP          NaN   
44     803  23018            CAP          NaN   
45     804  23019            CAP            4   
46     805  23020            CAP          NaN   
47     806  23021            CAP          NaN   
48     807  23022            CAP            5   
49     808  23023            CAP            6   
50     809  23024            CAP          NaN   
51     810  23025            CAP          NaN   
52     811  23026            CAP          NaN   
53     813  23028            CAP          NaN   
54     814  23029            CAP          NaN   
55     788  23003            CAP          NaN   
56     789  23004            CAP            1   
57     790  23005            CAP            2   
58     791  23006            CAP          NaN   
59     792  23007            CAP          NaN   
60     793  23008            CAP          NaN   
61     794  23009            CAP          NaN   
62     795  23010            CAP          NaN   
63     796  23011            CAP          NaN   
64     797  23012            CAP          NaN   
65     798  23013            CAP          NaN   
66     798  23013            CAP          NaN   
67     798  23013            CAP          NaN   
68     799  23014            CAP            3   
69     800  23015            CAP          NaN   
70     801  23016            CAP          NaN   
71     802  23017            CAP          NaN   
72     803  23018            CAP          NaN   
73     804  23019            CAP            4   
74     805  23020            CAP          NaN   
75     806  23021            CAP          NaN   
76     807  23022            CAP            5   
77     808  23023            CAP            6   
78     809  23024            CAP          NaN   
79     810  23025            CAP          NaN   
80     811  23026            CAP    

In [326]:
documentAnnotationObj = DocumentAnnotation('Kalydeco II-86-PI-clean_SmPC.json','c270d6ccaf9e47e9b20b322e2383c4ba','https://spor-uat.azure-api.net/pms/api/v2/',df,coll)

In [327]:
documentAnnotationObj.processRegulatedAuthorizationForDoc()

 ['EU/1/12/782/001', 'EU/1/12/782/002', 'EU/1/12/782/005', 'EU/1/12/782/003', 'EU/1/12/782/004', 'EU/1/12/782/006']
EU/1/12/782/001


MissingKeyValuePair: Missing Key 'entry' in the regulated authorization API output

In [328]:
documentAnnotationObj.processRegulatedAuthorizationForDoc(['EU/3/00/001','EU/1/97/039/003'])

EU/3/00/001
Skipping entry due to incorrect code 220000000062
No Regulated Authorization find with code 220000000061
Skipping entry due to incorrect code 220000000062
No Regulated Authorization find with code 220000000061
Skipping entry due to incorrect code 220000000062
No Regulated Authorization find with code 220000000061
EU/1/97/039/003
Found entry with code 220000000061
['0', '600000034241']
Cystagon 150 mg - Capsule, hard


[('0', '600000034241', 'Cystagon 150 mg - Capsule, hard')]

# End-To-End Flow 

In [267]:
def parseDocuments(procedureType,
                   languageCode,
                   documentNumber,
                   docFilter,
                   fileNameQrd,
                   fileNameMatchRuleBook,
                   fileNameDocumentTypeNames,
                   stopWordFilterLen=6,
                   start=0,
                   end=10,
                   isPackageLeaflet=False,
                   medName=None):

    '''
    This function was created to run the match function on multiple documents in automated fashion.
    
    '''

    if documentNumber == 0:
        topHeadingsConsidered=4
        bottomHeadingsConsidered=6
    elif documentNumber == 1:
        topHeadingsConsidered=3
        bottomHeadingsConsidered=5
    elif documentNumber == 2:
        topHeadingsConsidered=5
        bottomHeadingsConsidered=15
    else:
        topHeadingsConsidered=5
        bottomHeadingsConsidered=10
                
    path_json = os.path.join(os.path.abspath(os.path.join('..')), 'data', 'partitionedJSONs',f'{languageCode}')
    print(path_json)
    _,_,fileNames = next(os.walk(path_json))
    print(fileNames)
    filteredNames = [ fileName for fileName in fileNames if docFilter in fileName]
    filteredNames = filteredNames[start:end]
    print(filteredNames)
    for fileNameDoc in filteredNames:
        
        print(f"Starting Heading Extraction For File :- {fileNameDoc}")
        matchDocObj = MatchDocument(procedureType,
                 languageCode,
                 documentNumber,
                 fileNameDoc,
                 fileNameQrd,
                 fileNameMatchRuleBook,
                 fileNameDocumentTypeNames,
                 topHeadingsConsidered,
                 bottomHeadingsConsidered,
                 stopWordFilterLen,
                 stopWordlanguage,
                 isPackageLeaflet,
                 medName)
        df, coll = matchDocObj.matchHtmlHeaddingsWithQrd()
        
        print(f"Completed Heading Extraction For File")
        
        print(f"Starting Document Annotation For File :- {fileNameDoc}")        
        documentAnnotationObj = DocumentAnnotation(fileNameDoc,'c20835db4b1b4e108828a8537ff41506','https://spor-sit.azure-api.net/pms/api/v2/',df,coll)
        try:
            documentAnnotationObj.processRegulatedAuthorizationForDoc()
        
        except:
            print("Error Found")
            
        print(f"Completed Document Annotation For File")        

        print(f"Starting Extracting Content Between Heading For File :- {fileNameDoc}")        

        extractContentlogger = loggerCreator('ExtractContentBetween_'+ getRandomString(1))
        extractorObj = DataBetweenHeadingsExtractor(extractContentlogger, coll, languageCode)
        dfExtractedHierRR = extractorObj.extractContentBetweenHeadings(fileNameDoc)
        
        print(f"Completed Extracting Content Between Heading")        
        
        xmlLogger = loggerCreator('XmlGeneration_'+ getRandomString(1))
        fhirXmlGeneratorObj = FhirXmlGenerator(xmlLogger)
        fileNameXml = fileNameDoc.replace('.json','.xml')
        fhirXmlGeneratorObj.generateXml(dfExtractedHierRR,  fileNameXml)
        
        print(f"Created XML File For :- {fileNameDoc}")        


        return df,coll,dfExtractedHierRR


In [251]:
####
#Comman Parameters
procedureType = 'CAP'
fileNameQrd = 'qrd_canonical_mode_CAP_NAP.csv'
fileNameMatchRuleBook = 'ruleDict.json'
fileNameDocumentTypeNames = 'documentTypeNames.json'

## Spanish

In [252]:
languageCode = 'es'

### Kalydeco



### SmPC

In [253]:
documentNumber = 0
docFilter = "SmPC.json"
stopWordFilterLen = 6
stopWordlanguage = 'spanish'
start=0
end=1

In [254]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es
['emea-combined-h-2494-es_ PROSPECTO.json', 'emea-combined-h-2494-es_ANEXO II.json', 'emea-combined-h-2494-es_ANEXO III.json', 'emea-combined-h-2494-es_SmPC.json']
['emea-combined-h-2494-es_SmPC.json']
Starting Heading Extraction For File :- emea-combined-h-2494-es_SmPC.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_SmPC.json
--------------------------------------------
SmPC
----------------------------------
RemovedByStyle  ||    ||  FICHA TÉCNICA O RESUMEN DE LAS CARACTERÍSTICAS DEL PRODUCTO  ||  FICHA TÉCNICA O RESUMEN DE LAS CARACTERÍSTICAS DEL PRODUCTO
----------------------------------
True  ||    ||  1.       NOMBRE DEL MEDICAMENTO  ||  1. NOMBRE DEL MEDICAMENTO
True  ||    ||  2.       COMPOSICIÓN CUALITATIVA Y CUANTITATIVA  ||  2. COMPOSICIÓN CUALITATIVA Y CUANTITATIVA
True  ||  <=4|10.0|(95, 90, 95)|0.99|  ||  Excipien

True  ||    ||  Biotransformación  ||  Biotransformación
True  ||    ||  Eliminación  ||  Eliminación
True  ||    ||  Linealidad/No linealidad  ||  Linealidad/No linealidad
True  ||    ||  5.3     Datos preclínicos sobre seguridad  ||  5.3 Datos preclínicos sobre seguridad
True  ||    ||  6.       DATOS FARMACÉUTICOS  ||  6. DATOS FARMACÉUTICOS
True  ||    ||  6.1     Lista de excipientes  ||  6.1 Lista de excipientes
True  ||    ||  6.2     Incompatibilidades  ||  6.2 Incompatibilidades
True  ||    ||  6.3     Periodo de validez  ||  6.3 Periodo de validez
True  ||    ||  6.4     Precauciones especiales de conservación  ||  6.4 Precauciones especiales de conservación
True  ||  SpecialCase1|178.38|(47, 84, 86)|0.7|  ||  6.5     Naturaleza y contenido del envase  ||  6.5 Naturaleza y contenido del envase <y de los equipos especiales para su utilización, administración o implantación>
True  ||  SpecialCase2|7.41|(96, 94, 97)|0.99|  ||  6.6     Precauciones especiales de eliminación y otr

2021-04-26 00:32:46,040 : ExtractContentBetween_G : Cleaning Match Results
2021-04-26 00:32:46,044 : ExtractContentBetween_G : Finished Cleaning Match Results
2021-04-26 00:32:46,090 : ExtractContentBetween_G : Extracting Content Between Headings
2021-04-26 00:32:46,120 : ExtractContentBetween_G : Finished Extracting Content Between Headings


Error Found
Completed Document Annotation For File
Starting Extracting Content Between Heading For File :- emea-combined-h-2494-es_SmPC.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_SmPC.json
--------------------------------------------


index     id Procedure type Display code  \
0     818  24003            CAP            1   
1     819  24004            CAP            2   
2     822  24007            CAP          NaN   
3     822  24007            CAP          NaN   
4     823  24008            CAP            3   
5     824  24009            CAP            4   
6     825  24010            CAP          4.1   
7     826  24011            CAP          4.2   
8     827  24012            CAP          NaN   
9     828  24013            CAP          NaN   
10    829  24014            CAP          NaN   
11    831  24016            CAP          4.3   
12    832  24017            CAP          4.4   
13    834  24019            CAP          NaN   
14    835  24020            CAP          4.5   
15    836  24021            CAP          NaN   
16    837  24022            CAP          4.6   
17    838  24023            CAP          NaN   
18    839  24024            CAP          NaN   
19    840  24025            CAP          NaN   
20    841  24026            CAP          4.7   
21    842  24027            CAP          4.8   
22    843  24028            CAP          NaN   
23    844  24029            CAP          NaN   
24    845  24030            CAP          4.9   
25    847  24032            CAP            5   
26    848  24033            CAP          5.1   
27    849  24034            CAP          NaN   
28    850  24035            CAP          NaN   
29    851  24036            CAP          NaN   
30    852  24037            CAP          NaN   
31    853  24038            CAP          5.2   
32    854  24039            CAP          NaN   
33    855  24040            CAP          NaN   
34    856  24041            CAP          NaN   
35    857  24042            CAP          NaN   
36    858  24043            CAP          NaN   
37    860  24045            CAP          5.3   
38    862  24047            CAP            6   
39    863  24048            CAP          6.1   
40    864  24049            CAP          6.2   
41    865  24050            CAP          6.3   
42    866  24051            CAP          6.4   
43    867  24052            CAP          6.5   
44    868  24053            CAP          6.6   
45    870  24055            CAP            7   
46    871  24056            CAP            8   
47    872  24057            CAP            9   
48    873  24058            CAP           10   
49    818  24003            CAP            1   
50    819  24004            CAP            2   
51    822  24007            CAP          NaN   
52    822  24007            CAP          NaN   
53    822  24007            CAP          NaN   
54    823  24008            CAP            3   
55    824  24009            CAP            4   
56    825  24010            CAP          4.1   
57    826  24011            CAP          4.2   
58    827  24012            CAP          NaN   
59    828  24013            CAP          NaN   
60    829  24014            CAP          NaN   
61    831  24016            CAP          4.3   
62    832  24017            CAP          4.4   
63    834  24019            CAP          NaN   
64    835  24020            CAP          4.5   
65    836  24021            CAP          NaN   
66    837  24022            CAP          4.6   
67    838  24023            CAP          NaN   
68    839  24024            CAP          NaN   
69    840  24025            CAP          NaN   
70    841  24026            CAP          4.7   
71    842  24027            CAP          4.8   
72    843  24028            CAP          NaN   
73    844  24029            CAP          NaN   
74    845  24030            CAP          4.9   
75    847  24032            CAP            5   
76    848  24033            CAP          5.1   
77    849  24034            CAP          NaN   
78    850  24035            CAP          NaN   
79    851  24036            CAP          NaN   
80    852  24037            CAP          NaN   
81    853  24038            CAP          5.2   
82    854  24039    

2021-04-26 00:32:46,217 : XmlGeneration_A : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 00:32:46,569 : XmlGeneration_A : Writing to File:emea-combined-h-2494-es_SmPC.xml


Created XML File For :- emea-combined-h-2494-es_SmPC.json


### Annex II

In [257]:
documentNumber = 1
docFilter = "ANEXO II.json"
stopWordFilterLen = 6
stopWordlanguage = 'spanish'
start=0
end=1

In [258]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es
['emea-combined-h-2494-es_ PROSPECTO.json', 'emea-combined-h-2494-es_ANEXO II.json', 'emea-combined-h-2494-es_ANEXO III.json', 'emea-combined-h-2494-es_SmPC.json']
['emea-combined-h-2494-es_ANEXO II.json']
Starting Heading Extraction For File :- emea-combined-h-2494-es_ANEXO II.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_ANEXO II.json
--------------------------------------------
AnnexII
True  ||    ||  ANEXO II  ||  ANEXO II
True  ||  Contains<>|131.25|(60, 96, 88)|0.8|  ||  A.         FABRICANTE(S) RESPONSABLE(S) DE LA LIBERACIÓN DE LOS LOTES  ||  A. <FABRICANTE(S) DEL (DE LOS) PRINCIPIO(S) ACTIVO(S) BIOLÓGICO(S) Y> FABRICANTE(S) RESPONSABLE(S) DE LA LIBERACIÓN DE LOS LOTES
True  ||    ||  B.         CONDICIONES O RESTRICCIONES DE SUMINISTRO Y USO  ||  B. CONDICIONES O RESTRICCIONES DE SUMINISTRO Y USO 
True  ||    ||  C.   

2021-04-26 00:32:50,323 : ExtractContentBetween_F : Cleaning Match Results
2021-04-26 00:32:50,327 : ExtractContentBetween_F : Finished Cleaning Match Results
2021-04-26 00:32:50,335 : ExtractContentBetween_F : Extracting Content Between Headings
2021-04-26 00:32:50,342 : ExtractContentBetween_F : Finished Extracting Content Between Headings


Error Found
Completed Document Annotation For File
Starting Extracting Content Between Heading For File :- emea-combined-h-2494-es_ANEXO II.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_ANEXO II.json
--------------------------------------------


index     id Procedure type Display code  \
0     876  25001            CAP          NaN   
1     877  25002            CAP            A   
2     880  25005            CAP            B   
3     882  25007            CAP            C   
4     884  25009            CAP            D   
5     877  25002            CAP            A   
6     879  25004            CAP          NaN   
7     880  25005            CAP            B   
8     882  25007            CAP            C   
9     883  25008            CAP          NaN   
10    884  25009            CAP            D   
11    885  25010            CAP          NaN   
12    887  25012            CAP          NaN   

                                                                                                                             Name  \
0                                                                                                                        ANEXO II   
1   <FABRICANTE(S) DEL (DE LOS) PRINCIPIO(S) ACTIVO(S) BIOLÓGICO(S) Y> FABRICANTE(S) RESPONSABLE(S) DE LA LIBERACIÓN DE LOS LOTES   
2                                                                                CONDICIONES O RESTRICCIONES DE SUMINISTRO Y USO    
3                                                           OTRAS CONDICIONES Y REQUISITOS DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN   
4                                    CONDICIONES O RESTRICCIONES EN RELACIÓN CON LA UTILIZACIÓN SEGURA Y EFICAZ DEL MEDICAMENTO     
5   <FABRICANTE(S) DEL (DE LOS) PRINCIPIO(S) ACTIVO(S) BIOLÓGICO(S) Y> FABRICANTE(S) RESPONSABLE(S) DE LA LIBERACIÓN DE LOS LOTES   
6                                      Nombre y dirección del (de los) fabricante(s) responsable(s) de la liberación de los lotes   
7                                                                                CONDICIONES O RESTRICCIONES DE SUMINISTRO Y USO    
8                                                           OTRAS CONDICIONES Y REQUISITOS DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN   
9                                                                                         Informes periódicos de seguridad (IPSs)   
10                                   CONDICIONES O RESTRICCIONES EN RELACIÓN CON LA UTILIZACIÓN SEGURA Y EFICAZ DEL MEDICAMENTO     
11                                                                                               Plan de gestión de riesgos (PGR)   
12                                                                            Obligación de llevar a cabo medidas posautorización   

   parent_id  \
0        NaN   
1      25001   
2      25001   
3      25001   
4      25001   
5      25001   
6      25002   
7      25001   
8      25001   
9      25007   
10     25001   
11     25009   
12     25009   

                                                                                                 htmlText  \
0                                                                                                ANEXO II   
1                                   A.         FABRICANTE(S) RESPONSABLE(S) DE LA LIBERACIÓN DE LOS LOTES   
2                                              B.         CONDICIONES O RESTRICCIONES DE SUMINISTRO Y USO   
3                        C.         OTRAS CONDICIONES Y REQUISITOS DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN   
4   D.         CONDICIONES O RESTRICCIONES EN RELACIÓN CON LA UTILIZACIÓN SEGURA Y EFICAZ DEL MEDICAMENTO   
5                                     A.       FABRICANTE(S) RESPONSABLE(S) DE LA LIBERACIÓN DE LOS LOTES   
6              Nombre y dirección del (de los) fabricante(s) responsable(s) de la liberación de los lotes   
7                                                B.       CONDICIONES O RESTRICCIONES DE SUMINISTRO Y USO   
8                          C.       OTRAS CONDICIONES Y REQUISITOS DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN   
9                                                   ·             Informes periódicos de seguridad (IPSs)   
10    D.       CONDICIONES O RESTRICCIONES E

2021-04-26 00:32:50,369 : XmlGeneration_A : Initiating XML Generation
2021-04-26 00:32:50,369 : XmlGeneration_A : Initiating XML Generation
2021-04-26 00:32:50,407 : XmlGeneration_A : Writing to File:emea-combined-h-2494-es_ANEXO II.xml
2021-04-26 00:32:50,407 : XmlGeneration_A : Writing to File:emea-combined-h-2494-es_ANEXO II.xml


Completed Extracting Content Between Heading
Created XML File For :- emea-combined-h-2494-es_ANEXO II.json


### Labeling

In [259]:
documentNumber = 2
docFilter = "ANEXO III.json"
stopWordFilterLen = 6
stopWordlanguage = 'spanish'
start=0
end=1

In [260]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es
['emea-combined-h-2494-es_ PROSPECTO.json', 'emea-combined-h-2494-es_ANEXO II.json', 'emea-combined-h-2494-es_ANEXO III.json', 'emea-combined-h-2494-es_SmPC.json']
['emea-combined-h-2494-es_ANEXO III.json']
Starting Heading Extraction For File :- emea-combined-h-2494-es_ANEXO III.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_ANEXO III.json
--------------------------------------------
Labelling
True  ||  <=1|23.08|(87, 100, 95)|0.95|  ||  A. ETIQUETADO  ||  ETIQUETADO
True  ||  Contains<>|92.86|(68, 90, 86)|0.88|  ||  INFORMACIÓN QUE DEBE FIGURAR EN EL EMBALAJE EXTERIOR  ||  INFORMACIÓN QUE DEBE FIGURAR EN <EL EMBALAJE EXTERIOR><Y><EL ACONDICIONAMIENTO PRIMARIO>
True  ||    ||  1.       NOMBRE DEL MEDICAMENTO  ||  1. NOMBRE DEL MEDICAMENTO
True  ||    ||  2.       PRINCIPIO(S) ACTIVO(S)  ||  2. PRINCIPIO(S) ACTIVO(S)
True  ||   

True  ||    ||  8.       FECHA DE CADUCIDAD  ||  8. FECHA DE CADUCIDAD
True  ||    ||  9.       CONDICIONES ESPECIALES DE CONSERVACIÓN  ||  9. CONDICIONES ESPECIALES DE CONSERVACIÓN
True  ||    ||  10.     PRECAUCIONES ESPECIALES DE ELIMINACIÓN DEL MEDICAMENTO NO UTILIZADO Y DE LOS MATERIALES DERIVADOS DE SU USO, CUANDO CORRESPONDA  ||  10. PRECAUCIONES ESPECIALES DE ELIMINACIÓN DEL MEDICAMENTO NO UTILIZADO Y DE LOS MATERIALES DERIVADOS DE SU USO, CUANDO CORRESPONDA
True  ||    ||  11.     NOMBRE Y DIRECCIÓN DEL TITULAR DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN  ||  11. NOMBRE Y DIRECCIÓN DEL TITULAR DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN
True  ||    ||  12.     NÚMERO(S) DE AUTORIZACIÓN DE COMERCIALIZACIÓN  ||  12. NÚMERO(S) DE AUTORIZACIÓN DE COMERCIALIZACIÓN 
True  ||  Contains<>|166.67|(48, 83, 86)|0.83|  ||  13.     NÚMERO DE LOTE  ||  13. NÚMERO DE LOTE <, CÓDIGO DE DONACIÓN Y DEL PRODUCTO >
True  ||    ||  14.     CONDICIONES GENERALES DE DISPENSACIÓN  ||  14. CONDICIONES GENERALES

True  ||    ||  3.       FECHA DE CADUCIDAD  ||  3. FECHA DE CADUCIDAD
True  ||  Contains<>|176.47|(46, 82, 86)|0.82|  ||  4.       NÚMERO DE LOTE  ||  4. NÚMERO DE LOTE <, CÓDIGO DE DONACIÓN Y DEL PRODUCTO >
True  ||    ||  5.       OTROS  ||  5. OTROS
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  Contains<>|92.86|(68, 90, 86)|0.88|  ||  INFORMACIÓN QUE DEBE FIGURAR EN EL EMBALAJE EXTERIOR  ||  INFORMACIÓN QUE DEBE FIGURAR EN <EL EMBALAJE EXTERIOR><Y><EL ACONDICIONAMIENTO PRIMARIO>
True  ||    ||  1.       NOMBRE DEL MEDICAMENTO  ||  1. NOMBRE DEL MEDICAMENTO
True  ||    ||  2.       PRINCIPIO(S) ACTIVO(S)  ||  2. PRINCIPIO(S) ACTIVO(S)
True  ||    ||  3.       LISTA DE EXCIPIENTES  ||  3. LISTA DE EXCIPIENTES
True  ||    ||  4.       FORMA FARMACÉUTICA Y CONTENIDO DEL ENVASE  ||  4. FORMA FARMACÉUTICA Y CONTENIDO DEL ENVASE
True  ||    ||  5.       FORMA Y VÍA(S) DE ADMINISTRACIÓN  ||  5. FORMA Y VÍA

True  ||    ||  17.     IDENTIFICADOR ÚNICO - CÓDIGO DE BARRAS 2D  ||  17. IDENTIFICADOR ÚNICO - CÓDIGO DE BARRAS 2D

OriginalCheck
('<=7|92.31|(13, 12, 91)|0.35|', 'Incluido el código de barras 2D que lleva el identificador único.', '17. IDENTIFICADOR ÚNICO - CÓDIGO DE BARRAS 2D')

True  ||    ||  18.     IDENTIFICADOR ÚNICO - INFORMACIÓN EN CARACTERES VISUALES  ||  18. IDENTIFICADOR ÚNICO - INFORMACIÓN EN CARACTERES VISUALES
-------------------Here1------------------------
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  Contains<>|69.81|(70, 64, 86)|0.92|  ||  INFORMACIÓN QUE DEBE FIGURAR EN EL ACONDICIONAMIENTO INTERMEDIO  ||  INFORMACIÓN QUE DEBE FIGURAR EN <EL EMBALAJE EXTERIOR><Y><EL ACONDICIONAMIENTO PRIMARIO>
True  ||    ||  1.       NOMBRE DEL MEDICAMENTO  ||  1. NOMBRE DEL MEDICAMENTO
True  ||    ||  2.       PRINCIPIO(S) ACTIVO(S)  ||  2. PRINCIPIO(S) ACTIVO(S)
True  ||    ||  3.       LISTA D

True  ||    ||  9.       CONDICIONES ESPECIALES DE CONSERVACIÓN  ||  9. CONDICIONES ESPECIALES DE CONSERVACIÓN
True  ||    ||  10.     PRECAUCIONES ESPECIALES DE ELIMINACIÓN DEL MEDICAMENTO NO UTILIZADO Y DE LOS MATERIALES DERIVADOS DE SU USO, CUANDO CORRESPONDA  ||  10. PRECAUCIONES ESPECIALES DE ELIMINACIÓN DEL MEDICAMENTO NO UTILIZADO Y DE LOS MATERIALES DERIVADOS DE SU USO, CUANDO CORRESPONDA
True  ||    ||  11.     NOMBRE Y DIRECCIÓN DEL TITULAR DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN  ||  11. NOMBRE Y DIRECCIÓN DEL TITULAR DE LA AUTORIZACIÓN DE COMERCIALIZACIÓN
True  ||    ||  12.     NÚMERO(S) DE AUTORIZACIÓN DE COMERCIALIZACIÓN  ||  12. NÚMERO(S) DE AUTORIZACIÓN DE COMERCIALIZACIÓN 
True  ||  Contains<>|166.67|(48, 83, 86)|0.83|  ||  13.     NÚMERO DE LOTE  ||  13. NÚMERO DE LOTE <, CÓDIGO DE DONACIÓN Y DEL PRODUCTO >
True  ||    ||  14.     CONDICIONES GENERALES DE DISPENSACIÓN  ||  14. CONDICIONES GENERALES DE DISPENSACIÓN
True  ||    ||  15.     INSTRUCCIONES DE USO  ||  15. 

...

index     id Procedure type Display code  \
0      889  26001            CAP          NaN   
1      890  26002            CAP          NaN   
2      891  26003            CAP            1   
3      892  26004            CAP            2   
4      893  26005            CAP            3   
5      894  26006            CAP            4   
6      895  26007            CAP            5   
7      896  26008            CAP            6   
8      897  26009            CAP            7   
9      898  26010            CAP            8   
10     899  26011            CAP            9   
11     900  26012            CAP           10   
12     901  26013            CAP           11   
13     902  26014            CAP           12   
14     903  26015            CAP           13   
15     904  26016            CAP           14   
16     905  26017            CAP           15   
17     906  26018            CAP           16   
18     907  26019            CAP           17   
19     908  26020            CAP           18   
20     909  26021            CAP          NaN   
21     910  26022            CAP            1   
22     911  26023            CAP            2   
23     912  26024            CAP            3   
24     913  26025            CAP            4   
25     914  26026            CAP            5   
26     890  26002            CAP          NaN   
27     891  26003            CAP            1   
28     892  26004            CAP            2   
29     893  26005            CAP            3   
30     894  26006            CAP            4   
31     895  26007            CAP            5   
32     896  26008            CAP            6   
33     897  26009            CAP            7   
34     898  26010            CAP            8   
35     899  26011            CAP            9   
36     900  26012            CAP           10   
37     901  26013            CAP           11   
38     902  26014            CAP           12   
39     903  26015            CAP           13   
40     904  26016            CAP           14   
41     905  26017            CAP           15   
42     906  26018            CAP           16   
43     907  26019            CAP           17   
44     908  26020            CAP           18   
45     890  26002            CAP          NaN   
46     891  26003            CAP            1   
47     892  26004            CAP            2   
48     893  26005            CAP            3   
49     894  26006            CAP            4   
50     895  26007            CAP            5   
51     896  26008            CAP            6   
52     897  26009            CAP            7   
53     898  26010            CAP            8   
54     899  26011            CAP            9   
55     900  26012            CAP           10   
56     901  26013            CAP           11   
57     902  26014            CAP           12   
58     903  26015            CAP           13   
59     904  26016            CAP           14   
60     905  26017            CAP           15   
61     906  26018            CAP           16   
62     907  26019            CAP           17   
63     908  26020            CAP           18   
64     909  26021            CAP          NaN   
65     910  26022            CAP            1   
66     911  26023            CAP            2   
67     912  26024            CAP            3   
68     913  26025            CAP            4   
69     914  26026            CAP            5   
70     890  26002            CAP          NaN   
71     891  26003            CAP            1   
72     892  26004            CAP            2   
73     893  26005            CAP            3   
74     894  26006            CAP            4   
75     895  26007            CAP            5   
76     896  26008            CAP            6   
77     897  26009            CAP            7   
78     898  26010            CAP            8   
79     899  26011            CAP            9   
80     900  26012            CAP    

2021-04-26 00:34:04,640 : XmlGeneration_y : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 00:34:05,157 : XmlGeneration_y : Writing to File:emea-combined-h-2494-es_ANEXO III.xml


Created XML File For :- emea-combined-h-2494-es_ANEXO III.json


### Package Leaflet

In [261]:

documentNumber = 3
docFilter = "PROSPECTO.json"
stopWordFilterLen = 100
stopWordlanguage = 'spanish'
start=0
end=1
isPackageLeaflet=True

In [262]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end,
               isPackageLeaflet,
               'Kalydeco'
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es
['emea-combined-h-2494-es_ PROSPECTO.json', 'emea-combined-h-2494-es_ANEXO II.json', 'emea-combined-h-2494-es_ANEXO III.json', 'emea-combined-h-2494-es_SmPC.json']
['emea-combined-h-2494-es_ PROSPECTO.json']
Starting Heading Extraction For File :- emea-combined-h-2494-es_ PROSPECTO.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\es\emea-combined-h-2494-es_ PROSPECTO.json
--------------------------------------------
Package leaflet
True  ||  <=1|25.0|(86, 100, 95)|0.95|  ||  B. PROSPECTO  ||  PROSPECTO
True  ||    ||  Contenido del prospecto  ||  Contenido del prospecto
----------------------------------
RemovedByStyle  ||    ||  1.    Qué es Kalydeco y para qué se utiliza  ||  1. Qué es Kalydeco y para qué se utiliza
----------------------------------
----------------------------------
RemovedByStyle  ||  Contains<>|14.55|(93, 85, 95)|0.98|  ||  2.    Qué 

True  ||  Contains<>|38.46|(78, 75, 88)|0.86|  ||  Efectos adversos adicionales en niños y adolescentes  ||  Otros efectos adversos en niños <y adolescentes>
True  ||    ||  Comunicación de efectos adversos  ||  Comunicación de efectos adversos
True  ||    ||  5.            Conservación de Kalydeco  ||  5. Conservación de Kalydeco
True  ||    ||  6.            Contenido del envase e información adicional  ||  6. Contenido del envase e información adicional
True  ||    ||  Composición de Kalydeco  ||  Composición de Kalydeco 
True  ||    ||  Aspecto del producto y contenido del envase  ||  Aspecto del producto y contenido del envase
True  ||  Contains<>|73.91|(73, 100, 90)|0.94|  ||  Titular de la autorización de comercialización  ||  Titular de la autorización de comercialización <y responsable de la fabricación>
True  ||  SpecialCase1|54.35|(79, 100, 90)|0.96|  ||  Fecha de la última revisión de este prospecto:  ||  Fecha de la última revisión de este prospecto: <{MM/AAAA}><{mes AAAA}

2021-04-26 00:36:54,033 : ExtractContentBetween_1 : Cleaning Match Results
2021-04-26 00:36:54,038 : ExtractContentBetween_1 : Finished Cleaning Match Results
2021-04-26 00:36:54,060 : ExtractContentBetween_1 : Extracting Content Between Headings
2021-04-26 00:36:54,084 : ExtractContentBetween_1 : Finished Extracting Content Between Headings




Heading Not Found 
 ['q Este medicamento está sujeto a seguimiento adicional, lo que agilizará la detección de nueva información sobre su seguridad. Puede contribuir comunicando los efectos adversos que pudiera usted tener. La parte final de la sección 4 incluye información sobre cómo comunicar estos efectos adversos.', 'X contiene {nombre del (de los) excipiente(s)}', 'Pueden solicitar más información respecto a este medicamento dirigiéndose al representante local del titular de la autorización de comercialización:', 'Esta información está destinada únicamente a profesionales sanitarios:']


dict_keys(['1. Qué es Kalydeco y para qué se utiliza', '2. Qué necesita saber antes de empezar a <tomar><usar> Kalydeco', '3. Cómo <tomar><usar> Kalydeco', '4. Posibles efectos adversos', '5. Conservación de Kalydeco', '6. Contenido del envase e información adicional', 'Kalydeco contiene {nombre del (de los) excipiente(s)}'])
Completed Heading Extraction For File
Starting Document Annotation For

index     id Procedure type Display code  \
0     922  27001            CAP          NaN   
1     924  27003            CAP          NaN   
2     925  27004            CAP            1   
3     926  27005            CAP            2   
4     927  27006            CAP          NaN   
5     928  27007            CAP          NaN   
6     929  27008            CAP          NaN   
7     930  27009            CAP          NaN   
8     931  27010            CAP          NaN   
9     932  27011            CAP          NaN   
10    933  27012            CAP          NaN   
11    935  27014            CAP            3   
12    936  27015            CAP          NaN   
13    937  27016            CAP          NaN   
14    938  27017            CAP          NaN   
15    939  27018            CAP          NaN   
16    940  27019            CAP            4   
17    941  27020            CAP          NaN   
18    942  27021            CAP          NaN   
19    943  27022            CAP            5   
20    944  27023            CAP            6   
21    945  27024            CAP          NaN   
22    946  27025            CAP          NaN   
23    947  27026            CAP          NaN   
24    949  27028            CAP          NaN   
25    950  27029            CAP          NaN   
26    924  27003            CAP          NaN   
27    925  27004            CAP            1   
28    926  27005            CAP            2   
29    927  27006            CAP          NaN   
30    928  27007            CAP          NaN   
31    930  27009            CAP          NaN   
32    931  27010            CAP          NaN   
33    933  27012            CAP          NaN   
34    935  27014            CAP            3   
35    937  27016            CAP          NaN   
36    940  27019            CAP            4   
37    941  27020            CAP          NaN   
38    942  27021            CAP          NaN   
39    943  27022            CAP            5   
40    944  27023            CAP            6   
41    945  27024            CAP          NaN   
42    946  27025            CAP          NaN   
43    947  27026            CAP          NaN   
44    949  27028            CAP          NaN   
45    950  27029            CAP          NaN   

                                                                                Name  \
0                                                                          PROSPECTO   
1                                                            Contenido del prospecto   
2                                                     Qué es X y para qué se utiliza   
3                              Qué necesita saber antes de empezar a <tomar><usar> X   
4                                                                   No <tome><use> X   
5                                                       Advertencias y precauciones    
6                                                             Niños <y adolescentes>   
7                                                             Otros medicamentos y X   
8                        <Uso><Toma> de X con <alimentos><y><,><bebidas><y><alcohol>   
9                                           Embarazo <y><,> lactancia <y fertilidad>   
10                                                      Conducción y uso de máquinas   
11                                                              Cómo <tomar><usar> X   
12                                                     Uso en niños <y adolescentes>   
13                                                 Si <toma><usa> más X del que debe   
14                                                         Si olvidó <tomar><usar> X   
15                                                Si interrumpe el tratamiento con X   
16                                                         Posibles efectos adversos   
17                                  Otros efectos adversos en niños <y adolescentes>   
18                                                  Comunicación de efectos

2021-04-26 00:36:54,158 : XmlGeneration_x : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 00:36:54,343 : XmlGeneration_x : Writing to File:emea-combined-h-2494-es_ PROSPECTO.xml


Created XML File For :- emea-combined-h-2494-es_ PROSPECTO.json


(      Bold               Classes  \
 0    False                  None   
 1    False         ['MsoNormal']   
 2    False         ['MsoNormal']   
 3    False         ['MsoNormal']   
 4    False         ['MsoNormal']   
 5    False         ['MsoNormal']   
 6    False         ['MsoNormal']   
 7    False         ['MsoNormal']   
 8    False         ['MsoNormal']   
 9    False         ['MsoNormal']   
 10   False         ['MsoNormal']   
 11   False         ['MsoNormal']   
 12   False         ['MsoNormal']   
 13   False         ['MsoNormal']   
 14   False         ['MsoNormal']   
 15   False         ['MsoNormal']   
 16   False         ['MsoNormal']   
 17   False         ['MsoNormal']   
 18   False         ['MsoNormal']   
 19   False         ['MsoNormal']   
 20   False         ['MsoNormal']   
 21   False         ['MsoNormal']   
 22   False         ['MsoNormal']   
 23   False         ['MsoNormal']   
 24   False         ['MsoNormal']   
 25    True            ['TitleA']   
 

## German

In [278]:
languageCode = 'de'

### Kalydeco



### SmPC

In [294]:
documentNumber = 0
docFilter = "SmPC.json"
stopWordFilterLen = 6
stopWordlanguage = 'german'
start=0
end=1

In [295]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de
['emea-combined-h-2494-de_ PACKUNGSBEILAGE.json', 'emea-combined-h-2494-de_ANHANG II.json', 'emea-combined-h-2494-de_ANHANG III.json', 'emea-combined-h-2494-de_SmPC.json']
['emea-combined-h-2494-de_SmPC.json']
Starting Heading Extraction For File :- emea-combined-h-2494-de_SmPC.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de\emea-combined-h-2494-de_SmPC.json
--------------------------------------------
SmPC
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
True  ||    ||  2.       QUALITATIVE UND QUANTITATIVE ZUSAMMENSETZUNG  ||  2. QUALITATIVE UND QUANTITATIVE ZUSAMMENSETZUNG
True  ||  <=7|11.63|(95, 88, 95)|0.97|  ||  Sonstiger Bestandteil mit bekannter Wirkung  ||  Sonstige(r) Bestandteil(e) mit bekannter Wirkung
True  ||  <=7|11.63|(95, 88, 95)|0.97|  ||  Sonstiger Bestandteil mit bekannter Wirkung  ||  Son

True  ||    ||  Biotransformation  ||  Biotransformation
True  ||    ||  Elimination  ||  Elimination
True  ||    ||  Linearität/Nicht-Linearität  ||  Linearität/Nicht-Linearität
True  ||    ||  5.3     Präklinische Daten zur Sicherheit  ||  5.3 Präklinische Daten zur Sicherheit
True  ||    ||  6.       PHARMAZEUTISCHE ANGABEN  ||  6. PHARMAZEUTISCHE ANGABEN
True  ||    ||  6.1     Liste der sonstigen Bestandteile  ||  6.1 Liste der sonstigen Bestandteile
True  ||    ||  6.2     Inkompatibilitäten  ||  6.2 Inkompatibilitäten
True  ||    ||  6.3     Dauer der Haltbarkeit  ||  6.3 Dauer der Haltbarkeit
True  ||    ||  6.4     Besondere Vorsichtsmaßnahmen für die Aufbewahrung  ||  6.4 Besondere Vorsichtsmaßnahmen für die Aufbewahrung
True  ||  SpecialCase1|180.0|(45, 77, 86)|0.67|  ||  6.5     Art und Inhalt des Behältnisses  ||  6.5 Art und Inhalt des Behältnisses <und spezielles Zubehör für den Gebrauch, die Anwendung oder die Implantation>
True  ||  SpecialCase2|8.22|(96, 93, 97)|0.97|

2021-04-26 01:34:33,793 : ExtractContentBetween_r : Cleaning Match Results
2021-04-26 01:34:33,793 : ExtractContentBetween_r : Cleaning Match Results
2021-04-26 01:34:33,799 : ExtractContentBetween_r : Finished Cleaning Match Results
2021-04-26 01:34:33,799 : ExtractContentBetween_r : Finished Cleaning Match Results
2021-04-26 01:34:33,829 : ExtractContentBetween_r : Extracting Content Between Headings
2021-04-26 01:34:33,829 : ExtractContentBetween_r : Extracting Content Between Headings
2021-04-26 01:34:33,853 : ExtractContentBetween_r : Finished Extracting Content Between Headings
2021-04-26 01:34:33,853 : ExtractContentBetween_r : Finished Extracting Content Between Headings


Error Found
Completed Document Annotation For File
Starting Extracting Content Between Heading For File :- emea-combined-h-2494-de_SmPC.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de\emea-combined-h-2494-de_SmPC.json
--------------------------------------------


index     id Procedure type Display code  \
0     410  12003            CAP            1   
1     411  12004            CAP            2   
2     414  12007            CAP          NaN   
3     414  12007            CAP          NaN   
4     415  12008            CAP            3   
5     416  12009            CAP            4   
6     417  12010            CAP          4.1   
7     418  12011            CAP          4.2   
8     419  12012            CAP          NaN   
9     420  12013            CAP          NaN   
10    421  12014            CAP          NaN   
11    423  12016            CAP          4.3   
12    427  12020            CAP          4.5   
13    428  12021            CAP          NaN   
14    429  12022            CAP          4.6   
15    430  12023            CAP          NaN   
16    431  12024            CAP          NaN   
17    432  12025            CAP          NaN   
18    433  12026            CAP          4.7   
19    434  12027            CAP          4.8   
20    435  12028            CAP          NaN   
21    436  12029            CAP          NaN   
22    437  12030            CAP          4.9   
23    439  12032            CAP            5   
24    440  12033            CAP          5.1   
25    441  12034            CAP          NaN   
26    442  12035            CAP          NaN   
27    443  12036            CAP          NaN   
28    444  12037            CAP          NaN   
29    445  12038            CAP          5.2   
30    446  12039            CAP          NaN   
31    447  12040            CAP          NaN   
32    448  12041            CAP          NaN   
33    449  12042            CAP          NaN   
34    450  12043            CAP          NaN   
35    452  12045            CAP          5.3   
36    454  12047            CAP            6   
37    455  12048            CAP          6.1   
38    456  12049            CAP          6.2   
39    457  12050            CAP          6.3   
40    458  12051            CAP          6.4   
41    459  12052            CAP          6.5   
42    460  12053            CAP          6.6   
43    462  12055            CAP            7   
44    463  12056            CAP            8   
45    464  12057            CAP            9   
46    465  12058            CAP           10   
47    410  12003            CAP            1   
48    411  12004            CAP            2   
49    414  12007            CAP          NaN   
50    414  12007            CAP          NaN   
51    414  12007            CAP          NaN   
52    415  12008            CAP            3   
53    416  12009            CAP            4   
54    417  12010            CAP          4.1   
55    418  12011            CAP          4.2   
56    419  12012            CAP          NaN   
57    420  12013            CAP          NaN   
58    421  12014            CAP          NaN   
59    423  12016            CAP          4.3   
60    427  12020            CAP          4.5   
61    428  12021            CAP          NaN   
62    429  12022            CAP          4.6   
63    430  12023            CAP          NaN   
64    431  12024            CAP          NaN   
65    432  12025            CAP          NaN   
66    433  12026            CAP          4.7   
67    434  12027            CAP          4.8   
68    435  12028            CAP          NaN   
69    436  12029            CAP          NaN   
70    437  12030            CAP          4.9   
71    439  12032            CAP            5   
72    440  12033            CAP          5.1   
73    441  12034            CAP          NaN   
74    442  12035            CAP          NaN   
75    443  12036            CAP          NaN   
76    444  12037            CAP          NaN   
77    445  12038            CAP          5.2   
78    446  12039            CAP          NaN   
79    447  12040            CAP          NaN   
80    448  12041            CAP          NaN   
81    449  12042            CAP          NaN   
82    450  12043    

2021-04-26 01:34:33,908 : XmlGeneration_7 : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 01:34:34,284 : XmlGeneration_7 : Writing to File:emea-combined-h-2494-de_SmPC.xml


Created XML File For :- emea-combined-h-2494-de_SmPC.json


In [288]:
from match.rulebook.matchRulebook import MatchRuleBook

rules= MatchRuleBook(
            fileNameRuleBook= fileNameMatchRuleBook,
            procedureType= procedureType,
            languageCode= languageCode,
            documentNumber= 0).ruleDict



### Annex II

In [297]:
documentNumber = 1
docFilter = "ANHANG II.json"
stopWordFilterLen = 6
stopWordlanguage = 'german'
start=0
end=1

In [298]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de
['emea-combined-h-2494-de_ PACKUNGSBEILAGE.json', 'emea-combined-h-2494-de_ANHANG II.json', 'emea-combined-h-2494-de_ANHANG III.json', 'emea-combined-h-2494-de_SmPC.json']
['emea-combined-h-2494-de_ANHANG II.json']
Starting Heading Extraction For File :- emea-combined-h-2494-de_ANHANG II.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de\emea-combined-h-2494-de_ANHANG II.json
--------------------------------------------
ANHANG II

OriginalCheck
('<=4|44.44|(56, 56, 100)|0.76|', 'ANhang II', 'ANHANG II')

True  ||    ||  ANhang II  ||  ANHANG II
True  ||  Contains<>|175.56|(53, 87, 86)|0.66|  ||  A.        HERSTELLER, DER  FÜR DIE CHARGENFREIGABE VERANTWORTLICH IST   ||  A. <HERSTELLER DES WIRKSTOFFS/DER WIRKSTOFFE BIOLOGISCHEN URSPRUNGS UND> HERSTELLER, DER (DIE) FÜR DIE CHARGENFREIGABE VERANTWORTLICH IST (SIND)
True  ||    ||  B.        BEDINGUNGEN ODER E

2021-04-26 01:44:54,263 : ExtractContentBetween_e : Cleaning Match Results
2021-04-26 01:44:54,268 : ExtractContentBetween_e : Finished Cleaning Match Results
2021-04-26 01:44:54,277 : ExtractContentBetween_e : Extracting Content Between Headings
2021-04-26 01:44:54,284 : ExtractContentBetween_e : Finished Extracting Content Between Headings



OriginalCheck
('<=4|77.67|(32, 40, 86)|0.55|', 'Der Inhaber der Genehmigung für das Inverkehrbringen schließt innerhalb des festgelegten Zeitrahmens folgende Maßnahmen ab:', 'Verpflichtung zur Durchführung von Maßnahmen nach der Zulassung ')



Heading Not Found 
 ['Name und Anschrift des (der) Hersteller(s) des Wirkstoffs/der Wirkstoffe biologischen Ursprungs', 'Amtliche Chargenfreigabe', 'Zusätzliche Maßnahmen zur Risikominimierung', 'SPEZIFISCHE VERPFLICHTUNG ZUM ABSCHLUSS VON MASSNAHMEN NACH DER ZULASSUNG <UNTER „BESONDEREN BEDINGUNGEN“> <UNTER „AUSSERGEWÖHNLICHEN UMSTÄNDEN“']


dict_keys([])
Completed Heading Extraction For File
Starting Document Annotation For File :- emea-combined-h-2494-de_ANHANG II.json
Error Found
Completed Document Annotation For File
Starting Extracting Content Between Heading For File :- emea-combined-h-2494-de_ANHANG II.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de\emea-combined-h-2494-de_ANHANG 

index     id Procedure type Display code  \
0     468  13001            CAP          NaN   
1     469  13002            CAP            A   
2     472  13005            CAP            B   
3     474  13007            CAP            C   
4     476  13009            CAP            D   
5     469  13002            CAP            A   
6     471  13004            CAP          NaN   
7     472  13005            CAP            B   
8     474  13007            CAP            C   
9     475  13008            CAP          NaN   
10    476  13009            CAP            D   
11    477  13010            CAP          NaN   
12    479  13012            CAP          NaN   

                                                                                                                                             Name  \
0                                                                                                                                       ANHANG II   
1   <HERSTELLER DES WIRKSTOFFS/DER WIRKSTOFFE BIOLOGISCHEN URSPRUNGS UND> HERSTELLER, DER (DIE) FÜR DIE CHARGENFREIGABE VERANTWORTLICH IST (SIND)   
2                                                                               BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE ABGABE UND DEN GEBRAUCH    
3                                                                      SONSTIGE BEDINGUNGEN UND AUFLAGEN DER GENEHMIGUNG FÜR DAS INVERKEHRBRINGEN   
4                                                       BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE SICHERE UND WIRKSAME ANWENDUNG DES ARZNEIMITTELS   
5   <HERSTELLER DES WIRKSTOFFS/DER WIRKSTOFFE BIOLOGISCHEN URSPRUNGS UND> HERSTELLER, DER (DIE) FÜR DIE CHARGENFREIGABE VERANTWORTLICH IST (SIND)   
6                                         Name und Anschrift des (der) Hersteller(s), der (die) für die Chargenfreigabe verantwortlich ist (sind)   
7                                                                               BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE ABGABE UND DEN GEBRAUCH    
8                                                                      SONSTIGE BEDINGUNGEN UND AUFLAGEN DER GENEHMIGUNG FÜR DAS INVERKEHRBRINGEN   
9                                                     Regelmäßig aktualisierte Unbedenklichkeitsberichte [Periodic Safety Update Reports (PSURs)]   
10                                                      BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE SICHERE UND WIRKSAME ANWENDUNG DES ARZNEIMITTELS   
11                                                                                                                    Risikomanagement-Plan (RMP)   
12                                                                               Verpflichtung zur Durchführung von Maßnahmen nach der Zulassung    

   parent_id  \
0        NaN   
1      13001   
2      13001   
3      13001   
4      13001   
5      13001   
6      13002   
7      13001   
8      13001   
9      13007   
10     13001   
11     13009   
12     13009   

                                                                                               htmlText  \
0                                                                                             ANhang II   
1                                A.        HERSTELLER, DER  FÜR DIE CHARGENFREIGABE VERANTWORTLICH IST    
2                            B.        BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE ABGABE UND DEN GEBRAUCH   
3                  C.        SONSTIGE BEDINGUNGEN UND AUFLAGEN DER GENEHMIGUNG FÜR DAS INVERKEHRBRINGEN   
4   D.        BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE SICHERE UND WIRKSAME ANWENDUNG DES ARZNEIMITTELS   
5                                   A.      HERSTELLER, DER FÜR DIE CHARGENFREIGABE VERANTWORTLICH IST    
6                   Name und Anschrift des Herstellers, der für die Chargenfreigabe verantwortlich ist    
7                              B.      BEDINGUNGEN ODER EINSCHRÄNKUNGEN FÜR DIE ABGABE UND DEN GEBRAUCH   
8                   C.      SONSTIGE BEDINGUNGEN UND AUF

2021-04-26 01:44:54,317 : XmlGeneration_g : Initiating XML Generation
2021-04-26 01:44:54,372 : XmlGeneration_g : Writing to File:emea-combined-h-2494-de_ANHANG II.xml


Completed Extracting Content Between Heading
Created XML File For :- emea-combined-h-2494-de_ANHANG II.json


### Labeling

In [302]:
documentNumber = 2
docFilter = "ANHANG III.json"
stopWordFilterLen = 6
stopWordlanguage = 'german'
start=0
end=1

In [303]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de
['emea-combined-h-2494-de_ PACKUNGSBEILAGE.json', 'emea-combined-h-2494-de_ANHANG II.json', 'emea-combined-h-2494-de_ANHANG III.json', 'emea-combined-h-2494-de_SmPC.json']
['emea-combined-h-2494-de_ANHANG III.json']
Starting Heading Extraction For File :- emea-combined-h-2494-de_ANHANG III.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de\emea-combined-h-2494-de_ANHANG III.json
--------------------------------------------
Etikettierung
True  ||  <=1|18.75|(90, 100, 95)|0.96|  ||  A. ETIKETTIERUNG  ||  ETIKETTIERUNG 
True  ||  Contains<>|82.35|(68, 88, 86)|0.9|  ||  ANGABEN AUF DER ÄUSSEREN UMHÜLLUNG  ||  ANGABEN <AUF DER ÄUSSEREN UMHÜLLUNG> <UND> <AUF DEM BEHÄLTNIS>
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
True  ||    ||  2.       WIRKSTOFF(E)  ||  2. WIRKSTOFF(E)
True  ||    ||  3.       SONSTIGE BESTAN

True  ||    ||  MINDESTANGABEN AUF BLISTERPACKUNGEN ODER FOLIENSTREIFEN  ||  MINDESTANGABEN AUF BLISTERPACKUNGEN ODER FOLIENSTREIFEN
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
True  ||    ||  2.       NAME DES PHARMAZEUTISCHEN UNTERNEHMERS  ||  2. NAME DES PHARMAZEUTISCHEN UNTERNEHMERS
True  ||    ||  3.       VERFALLDATUM  ||  3. VERFALLDATUM
True  ||  Contains<>|133.33|(60, 100, 90)|0.89|  ||  4.       CHARGENBEZEICHNUNG  ||  4. CHARGENBEZEICHNUNG<, SPENDER- UND PRODUKTCODE>
True  ||    ||  5.       WEITERE ANGABEN  ||  5. WEITERE ANGABEN
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  Contains<>|82.35|(68, 88, 86)|0.9|  ||  ANGABEN AUF DER ÄUSSEREN UMHÜLLUNG  ||  ANGABEN <AUF DER ÄUSSEREN UMHÜLLUNG> <UND> <AUF DEM BEHÄLTNIS>
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
True  ||    ||  2.       WIRKSTOFF(E

True  ||    ||  16.     ANGABEN IN BLINDENSCHRIFT  ||  16. ANGABEN IN BLINDENSCHRIFT
True  ||    ||  17.     INDIVIDUELLES ERKENNUNGSMERKMAL – 2D-BARCODE  ||  17. INDIVIDUELLES ERKENNUNGSMERKMAL – 2D-BARCODE
True  ||    ||  18.     INDIVIDUELLES ERKENNUNGSMERKMAL – VOM MENSCHEN LESBARES FORMAT  ||  18. INDIVIDUELLES ERKENNUNGSMERKMAL – VOM MENSCHEN LESBARES FORMAT
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||    ||  2.       WIRKSTOFF(E)  ||  2. WIRKSTOFF(E)
True  ||    ||  3.       SONSTIGE BESTANDTEILE  ||  3. SONSTIGE BESTANDTEILE
True  ||    ||  4.       DARREICHUNGSFORM UND INHALT  ||  4. DARREICHUNGSFORM UND INHALT

OriginalCheck
('<=4|24.14|(76, 76, 100)|0.89|', '5.       Hinweise zur UND ART(EN) DER ANWENDUNG', '5. HINWEISE ZUR UND ART(EN) DER ANWENDUNG')

----------------------------------
RemovedByStyl

True  ||    ||  5.       INHALT NACH GEWICHT, VOLUMEN ODER EINHEITEN  ||  5. INHALT NACH GEWICHT, VOLUMEN ODER EINHEITEN
True  ||    ||  6.       WEITERE ANGABEN  ||  6. WEITERE ANGABEN
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  Contains<>|82.35|(68, 88, 86)|0.9|  ||  ANGABEN AUF DER ÄUSSEREN UMHÜLLUNG  ||  ANGABEN <AUF DER ÄUSSEREN UMHÜLLUNG> <UND> <AUF DEM BEHÄLTNIS>
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
True  ||  <=4|25.0|(89, 100, 95)|0.97|  ||  2.       WIRKSTOFF  ||  2. WIRKSTOFF(E)
True  ||    ||  3.       SONSTIGE BESTANDTEILE  ||  3. SONSTIGE BESTANDTEILE
True  ||    ||  4.       DARREICHUNGSFORM UND INHALT  ||  4. DARREICHUNGSFORM UND INHALT

OriginalCheck
('<=4|24.14|(76, 76, 100)|0.89|', '5.       Hinweise zur UND ART(EN) DER ANWENDUNG', '5. HINWEISE ZUR UND ART(EN) DER ANWENDUNG')

----------------------------------
RemovedByStyle  

True  ||    ||  17.     INDIVIDUELLES ERKENNUNGSMERKMAL – 2D-BARCODE  ||  17. INDIVIDUELLES ERKENNUNGSMERKMAL – 2D-BARCODE
True  ||    ||  18.     INDIVIDUELLES ERKENNUNGSMERKMAL – VOM MENSCHEN LESBARES FORMAT  ||  18. INDIVIDUELLES ERKENNUNGSMERKMAL – VOM MENSCHEN LESBARES FORMAT
True  ||    ||  1.       BEZEICHNUNG DES ARZNEIMITTELS  ||  1. BEZEICHNUNG DES ARZNEIMITTELS
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  <=4|25.0|(89, 100, 95)|0.97|  ||  2.       WIRKSTOFF  ||  2. WIRKSTOFF(E)
True  ||    ||  3.       SONSTIGE BESTANDTEILE  ||  3. SONSTIGE BESTANDTEILE
True  ||    ||  4.       DARREICHUNGSFORM UND INHALT  ||  4. DARREICHUNGSFORM UND INHALT

OriginalCheck
('<=4|24.14|(76, 76, 100)|0.89|', '5.       Hinweise zur UND ART(EN) DER ANWENDUNG', '5. HINWEISE ZUR UND ART(EN) DER ANWENDUNG')

----------------------------------
RemovedByStyle  ||    ||  5.       Hinweise zur UND ART(EN) DER ANWENDUNG

...

index     id Procedure type Display code  \
0      481  14001            CAP          NaN   
1      482  14002            CAP          NaN   
2      483  14003            CAP            1   
3      484  14004            CAP            2   
4      485  14005            CAP            3   
5      486  14006            CAP            4   
6      488  14008            CAP            6   
7      489  14009            CAP            7   
8      490  14010            CAP            8   
9      491  14011            CAP            9   
10     492  14012            CAP           10   
11     493  14013            CAP           11   
12     494  14014            CAP           12   
13     496  14016            CAP           14   
14     497  14017            CAP           15   
15     498  14018            CAP           16   
16     499  14019            CAP           17   
17     500  14020            CAP           18   
18     501  14021            CAP          NaN   
19     502  14022            CAP            1   
20     503  14023            CAP            2   
21     504  14024            CAP            3   
22     506  14026            CAP            5   
23     482  14002            CAP          NaN   
24     483  14003            CAP            1   
25     484  14004            CAP            2   
26     485  14005            CAP            3   
27     486  14006            CAP            4   
28     487  14007            CAP            5   
29     488  14008            CAP            6   
30     489  14009            CAP            7   
31     490  14010            CAP            8   
32     491  14011            CAP            9   
33     492  14012            CAP           10   
34     493  14013            CAP           11   
35     494  14014            CAP           12   
36     495  14015            CAP           13   
37     496  14016            CAP           14   
38     497  14017            CAP           15   
39     498  14018            CAP           16   
40     499  14019            CAP           17   
41     500  14020            CAP           18   
42     502  14022            CAP            1   
43     484  14004            CAP            2   
44     485  14005            CAP            3   
45     486  14006            CAP            4   
46     487  14007            CAP            5   
47     488  14008            CAP            6   
48     489  14009            CAP            7   
49     490  14010            CAP            8   
50     491  14011            CAP            9   
51     492  14012            CAP           10   
52     493  14013            CAP           11   
53     494  14014            CAP           12   
54     495  14015            CAP           13   
55     496  14016            CAP           14   
56     497  14017            CAP           15   
57     498  14018            CAP           16   
58     499  14019            CAP           17   
59     500  14020            CAP           18   
60     501  14021            CAP          NaN   
61     502  14022            CAP            1   
62     503  14023            CAP            2   
63     504  14024            CAP            3   
64     505  14025            CAP            4   
65     506  14026            CAP            5   
66     482  14002            CAP          NaN   
67     483  14003            CAP            1   
68     484  14004            CAP            2   
69     485  14005            CAP            3   
70     486  14006            CAP            4   
71     487  14007            CAP            5   
72     488  14008            CAP            6   
73     489  14009            CAP            7   
74     490  14010            CAP            8   
75     491  14011            CAP            9   
76     492  14012            CAP           10   
77     493  14013            CAP           11   
78     494  14014            CAP           12   
79     495  14015            CAP           13   
80     496  14016            CAP    

2021-04-26 01:49:11,998 : XmlGeneration_Y : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 01:49:12,327 : XmlGeneration_Y : Writing to File:emea-combined-h-2494-de_ANHANG III.xml


Created XML File For :- emea-combined-h-2494-de_ANHANG III.json


In [304]:
a

Bold              Classes  \
0     False                 None   
1     False        ['MsoNormal']   
2     False        ['MsoNormal']   
3     False        ['MsoNormal']   
4     False        ['MsoNormal']   
5     False        ['MsoNormal']   
6     False        ['MsoNormal']   
7     False        ['MsoNormal']   
8     False        ['MsoNormal']   
9     False        ['MsoNormal']   
10    False        ['MsoNormal']   
11    False        ['MsoNormal']   
12    False        ['MsoNormal']   
13    False        ['MsoNormal']   
14    False        ['MsoNormal']   
15    False        ['MsoNormal']   
16    False        ['MsoNormal']   
17    False        ['MsoNormal']   
18    False        ['MsoNormal']   
19    False        ['MsoNormal']   
20    False        ['MsoNormal']   
21    False        ['MsoNormal']   
22    False        ['MsoNormal']   
23    False        ['MsoNormal']   
24     True        ['MsoNormal']   
25    False        ['MsoNormal']   
26     True        ['MsoNormal']   
27    False                 None   
28    False                 None   
29    False        ['MsoNormal']   
30    False        ['MsoNormal']   
31    False        ['MsoNormal']   
32    False        ['MsoNormal']   
33    False        ['MsoNormal']   
34    False        ['MsoNormal']   
35    False        ['MsoNormal']   
36    False        ['MsoNormal']   
37    False        ['MsoNormal']   
38    False        ['MsoNormal']   
39    False        ['MsoNormal']   
40    False        ['MsoNormal']   
41    False        ['MsoNormal']   
42    False        ['MsoNormal']   
43    False        ['MsoNormal']   
44    False        ['MsoNormal']   
45    False        ['MsoNormal']   
46    False        ['MsoNormal']   
47    False        ['MsoNormal']   
48    False        ['MsoNormal']   
49    False        ['MsoNormal']   
50    False                 None   
51    False                 None   
52     True           ['TitleA']   
53    False                 None   
54    False                 None   
55    False        ['MsoNormal']   
56    False                 None   
57     True        ['MsoNormal']   
58    False        ['MsoNormal']   
59     True        ['MsoNormal']   
60    False        ['MsoNormal']   
61    False        ['MsoNormal']   
62    False                 None   
63     True        ['MsoNormal']   
64    False        ['MsoNormal']   
65    False        ['MsoNormal']   
66    False        ['MsoNormal']   
67    False        ['MsoNormal']   
68    False        ['MsoNormal']   
69    False                 None   
70     True        ['MsoNormal']   
71    False        ['MsoNormal']   
72    False        ['MsoNormal']   
73    False        ['MsoNormal']   
74    False        ['MsoNormal']   
75    False                 None   
76     True        ['MsoNormal']   
77    False        ['MsoNormal']   
78    False        ['MsoNormal']   
79    False        ['MsoNormal']   
80    False        ['MsoNormal']   
81    False        ['MsoNormal']   
82    False        ['MsoNormal']   
83    False                 None   
84     True        ['MsoNormal']   
85    False        ['MsoNormal']   
86    False        ['MsoNormal']   
87    False        ['MsoNormal']   
88    False        ['MsoNormal']   
89    False                 None   
90     True        ['MsoNormal']   
91    False        ['MsoNormal']   
92    False        ['MsoNormal']   
93    False        ['MsoNormal']   
94    False        ['MsoNormal']   
95    False        ['MsoNormal']   
96     True        ['MsoNormal']   
97    False        ['MsoNormal']   
98    False        ['MsoNormal']   
99    False        ['MsoNormal']   
100   False        ['MsoNormal']   
101   False        ['MsoNormal']   
102   False        ['MsoNormal']   
103   False                 None   
104    True        ['MsoNormal']   
105   False        ['MsoNormal']   
106   False        ['MsoNormal']   
107   False        ['MsoNormal']   
108   False        ['MsoNormal']   
109   False                 None   
110    True

### Package Leaflet

In [314]:
documentNumber = 3
docFilter = "PACKUNGSBEILAGE.json"
stopWordFilterLen = 100
stopWordlanguage = 'german'
start=0
end=1
isPackageLeaflet = True

In [315]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end,
               isPackageLeaflet,
               "Kalydeco"
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de
['emea-combined-h-2494-de_ PACKUNGSBEILAGE.json', 'emea-combined-h-2494-de_ANHANG II.json', 'emea-combined-h-2494-de_ANHANG III.json', 'emea-combined-h-2494-de_SmPC.json']
['emea-combined-h-2494-de_ PACKUNGSBEILAGE.json']
Starting Heading Extraction For File :- emea-combined-h-2494-de_ PACKUNGSBEILAGE.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\de\emea-combined-h-2494-de_ PACKUNGSBEILAGE.json
--------------------------------------------
Packungsbeilage
True  ||  <=1|16.67|(91, 100, 95)|0.91|  ||  B. PACKUNGSBEILAGE  ||  PACKUNGSBEILAGE
True  ||    ||  Was in dieser Packungsbeilage steht  ||  Was in dieser Packungsbeilage steht
----------------------------------
RemovedByStyle  ||    ||  1.       Was ist Kalydeco und wofür wird es angewendet?  ||  1. Was ist Kalydeco und wofür wird es angewendet?
----------------------------------
----------------------

True  ||  Contains<>|46.88|(81, 97, 95)|0.96|  ||  3.       Wie ist Kalydeco einzunehmen?  ||  3. Wie ist Kalydeco <einzunehmen> <anzuwenden>?
True  ||  Contains<>|38.16|(81, 74, 80)|0.92|  ||  Wenn Ihr Kind eine größere Menge von Kalydeco eingenommen hat, als es sollte  ||  Wenn Sie eine größere Menge von Kalydeco <eingenommen> <angewendet> haben, als Sie sollten
True  ||    ||  4.       Welche Nebenwirkungen sind möglich?  ||  4. Welche Nebenwirkungen sind möglich?
True  ||  Contains<>|3.64|(98, 98, 99)|1.0|  ||  Zusätzliche Nebenwirkungen bei Kindern und Jugendlichen  ||  Zusätzliche Nebenwirkungen bei Kindern <und Jugendlichen>
True  ||    ||  Meldung von Nebenwirkungen  ||  Meldung von Nebenwirkungen
True  ||    ||  5.       Wie ist Kalydeco aufzubewahren?  ||  5. Wie ist Kalydeco aufzubewahren?
True  ||    ||  6.       Inhalt der Packung und weitere Informationen  ||  6. Inhalt der Packung und weitere Informationen
True  ||    ||  Was Kalydeco enthält  ||  Was Kalydeco enthält
Tr

2021-04-26 02:00:23,873 : ExtractContentBetween_4 : Cleaning Match Results
2021-04-26 02:00:23,879 : ExtractContentBetween_4 : Finished Cleaning Match Results
2021-04-26 02:00:23,902 : ExtractContentBetween_4 : Extracting Content Between Headings
2021-04-26 02:00:23,925 : ExtractContentBetween_4 : Finished Extracting Content Between Headings




Heading Not Found 
 ['q Dieses Arzneimittel unterliegt einer zusätzlichen Überwachung. Dies ermöglicht eine schnelle Identifizierung neuer Erkenntnisse über die Sicherheit. Sie können dabei helfen, indem Sie jede auftretende Nebenwirkung melden. Hinweise zur Meldung von Nebenwirkungen, siehe Ende Abschnitt 4', 'X enthält {Bezeichnung <des> <der> sonstigen Bestandteil(s)(e)}', 'Pharmazeutischer Unternehmer und Hersteller', 'Falls Sie weitere Informationen über das Arzneimittel wünschen, setzen Sie sich bitte mit dem örtlichen Vertreter des pharmazeutischen Unternehmers in Verbindung:', 'Die folgenden Informationen sind für medizinisches Fachpersonal bestimmt:']


dict_keys(['1. Was ist Kalydeco und wofür wird es angewendet?', '2. Was sollten Sie vor der <Einnahme> <Anwendung> von Kalydeco beachten?', '3. Wie ist Kalydeco <einzunehmen> <anzuwenden>?', '4. Welche Nebenwirkungen sind möglich?', '5. Wie ist Kalydeco aufzubewahren?', '6. Inhalt der Packung und weitere Informationen', 'Kaly

index     id Procedure type Display code  \
0     514  15001            CAP          NaN   
1     516  15003            CAP          NaN   
2     517  15004            CAP            1   
3     518  15005            CAP            2   
4     519  15006            CAP          NaN   
5     520  15007            CAP          NaN   
6     521  15008            CAP          NaN   
7     522  15009            CAP          NaN   
8     523  15010            CAP          NaN   
9     524  15011            CAP          NaN   
10    525  15012            CAP          NaN   
11    527  15014            CAP            3   
12    528  15015            CAP          NaN   
13    529  15016            CAP          NaN   
14    530  15017            CAP          NaN   
15    531  15018            CAP          NaN   
16    532  15019            CAP            4   
17    533  15020            CAP          NaN   
18    534  15021            CAP          NaN   
19    535  15022            CAP            5   
20    536  15023            CAP            6   
21    537  15024            CAP          NaN   
22    538  15025            CAP          NaN   
23    541  15028            CAP          NaN   
24    542  15029            CAP          NaN   
25    516  15003            CAP          NaN   
26    517  15004            CAP            1   
27    519  15006            CAP          NaN   
28    520  15007            CAP          NaN   
29    522  15009            CAP          NaN   
30    523  15010            CAP          NaN   
31    525  15012            CAP          NaN   
32    527  15014            CAP            3   
33    529  15016            CAP          NaN   
34    532  15019            CAP            4   
35    533  15020            CAP          NaN   
36    534  15021            CAP          NaN   
37    535  15022            CAP            5   
38    536  15023            CAP            6   
39    537  15024            CAP          NaN   
40    538  15025            CAP          NaN   
41    541  15028            CAP          NaN   
42    542  15029            CAP          NaN   

                                                                                                 Name  \
0                                                                                     PACKUNGSBEILAGE   
1                                                                 Was in dieser Packungsbeilage steht   
2                                                             Was ist X und wofür wird es angewendet?   
3                                      Was sollten Sie vor der <Einnahme> <Anwendung> von X beachten?   
4                                                   X darf nicht <eingenommen> <angewendet> werden<,>   
5                                                                 Warnhinweise und Vorsichtsmaßnahmen   
6                                                                            Kinder <und Jugendliche>   
7                                     <Einnahme> <Anwendung> von X zusammen mit anderen Arzneimitteln   
8   <Einnahme> <Anwendung> von X zusammen mit <Nahrungsmitteln> <und> <,> <Getränken> <und> <Alkohol>   
9                                   Schwangerschaft <und> <,> Stillzeit <und Fortpflanzungsfähigkeit>   
10                                       Verkehrstüchtigkeit und Fähigkeit zum Bedienen von Maschinen   
11                                                              Wie ist X <einzunehmen> <anzuwenden>?   
12                                                           Anwendung bei Kindern <und Jugendlichen>   
13                Wenn Sie eine größere Menge von X <eingenommen> <angewendet> haben, als Sie sollten   
14                                          Wenn Sie die <Einnahme> <Anwendung> von X vergessen haben   
15                                                Wenn Sie die <Einnahme> <Anwendung> von X abbrechen   
16                                                                Welche Nebenwirkungen sind möglich?   
1

2021-04-26 02:00:24,010 : XmlGeneration_W : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 02:00:24,362 : XmlGeneration_W : Writing to File:emea-combined-h-2494-de_ PACKUNGSBEILAGE.xml


Created XML File For :- emea-combined-h-2494-de_ PACKUNGSBEILAGE.json


## English

In [322]:
languageCode = 'en'

### Kalydeco



### SmPC

In [323]:
documentNumber = 0
docFilter = "SmPC.json"
stopWordFilterLen = 6
stopWordlanguage = 'english'
start=0
end=1

In [324]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en
['Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json', 'Kalydeco II-86-PI-clean_ANNEX II.json', 'Kalydeco II-86-PI-clean_ANNEX III.json', 'Kalydeco II-86-PI-clean_SmPC.json']
['Kalydeco II-86-PI-clean_SmPC.json']
Starting Heading Extraction For File :- Kalydeco II-86-PI-clean_SmPC.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_SmPC.json
--------------------------------------------
SmPC
----------------------------------
RemovedByStyle  ||    ||  SUMMARY OF PRODUCT CHARACTERISTICS  ||  SUMMARY OF PRODUCT CHARACTERISTICS
----------------------------------
True  ||    ||  1.       NAME OF THE MEDICINAL PRODUCT  ||  1. NAME OF THE MEDICINAL PRODUCT
True  ||    ||  2.       QUALITATIVE AND QUANTITATIVE COMPOSITION  ||  2. QUALITATIVE AND QUANTITATIVE COMPOSITION
True  ||  <=4|11.11|(95, 89, 95)|0.99|  ||  Excipient with known effect  ||  

True  ||    ||  6.2     Incompatibilities  ||  6.2 Incompatibilities
True  ||    ||  6.3       Shelf life  ||  6.3 Shelf life
True  ||    ||  6.4     Special precautions for storage  ||  6.4 Special precautions for storage
True  ||  SpecialCase1|158.33|(48, 81, 86)|0.69|  ||  6.5     Nature and contents of container  ||  6.5 Nature and contents of container <and special equipment for use administration or implantation>
True  ||  SpecialCase2|14.63|(93, 88, 95)|0.98|  ||  6.6     Special precautions for disposal and other handling  ||  6.6 Special precautions for disposal <and other handling>
True  ||    ||  7.       MARKETING AUTHORISATION HOLDER  ||  7. MARKETING AUTHORISATION HOLDER
True  ||    ||  8.       MARKETING AUTHORISATION NUMBER(S)  ||  8. MARKETING AUTHORISATION NUMBER(S)
True  ||    ||  9.       DATE OF FIRST AUTHORISATION/RENEWAL OF THE AUTHORISATION  ||  9. DATE OF FIRST AUTHORISATION/RENEWAL OF THE AUTHORISATION
True  ||    ||  10.     DATE OF REVISION OF THE TEXT  ||  

2021-04-26 02:19:51,614 : ExtractContentBetween_9 : Cleaning Match Results
2021-04-26 02:19:51,617 : ExtractContentBetween_9 : Finished Cleaning Match Results
2021-04-26 02:19:51,645 : ExtractContentBetween_9 : Extracting Content Between Headings
2021-04-26 02:19:51,665 : ExtractContentBetween_9 : Finished Extracting Content Between Headings


Error Found
Completed Document Annotation For File
Starting Extracting Content Between Heading For File :- Kalydeco II-86-PI-clean_SmPC.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_SmPC.json
--------------------------------------------


index     id Procedure type Display code  \
0     682  20003            CAP            1   
1     683  20004            CAP            2   
2     686  20007            CAP          NaN   
3     687  20008            CAP            3   
4     688  20009            CAP            4   
5     689  20010            CAP          4.1   
6     690  20011            CAP          4.2   
7     691  20012            CAP          NaN   
8     692  20013            CAP          NaN   
9     693  20014            CAP          NaN   
10    695  20016            CAP          4.3   
11    696  20017            CAP          4.4   
12    698  20019            CAP          NaN   
13    699  20020            CAP          4.5   
14    700  20021            CAP          NaN   
15    701  20022            CAP          4.6   
16    702  20023            CAP          NaN   
17    703  20024            CAP          NaN   
18    704  20025            CAP          NaN   
19    705  20026            CAP          4.7   
20    706  20027            CAP          4.8   
21    707  20028            CAP          NaN   
22    708  20029            CAP          NaN   
23    709  20030            CAP          4.9   
24    711  20032            CAP            5   
25    712  20033            CAP          5.1   
26    713  20034            CAP          NaN   
27    714  20035            CAP          NaN   
28    715  20036            CAP          NaN   
29    716  20037            CAP          NaN   
30    717  20038            CAP          5.2   
31    718  20039            CAP          NaN   
32    719  20040            CAP          NaN   
33    720  20041            CAP          NaN   
34    721  20042            CAP          NaN   
35    722  20043            CAP          NaN   
36    724  20045            CAP          5.3   
37    726  20047            CAP            6   
38    727  20048            CAP          6.1   
39    728  20049            CAP          6.2   
40    729  20050            CAP          6.3   
41    730  20051            CAP          6.4   
42    731  20052            CAP          6.5   
43    732  20053            CAP          6.6   
44    734  20055            CAP            7   
45    735  20056            CAP            8   
46    736  20057            CAP            9   
47    737  20058            CAP           10   
48    682  20003            CAP            1   
49    683  20004            CAP            2   
50    686  20007            CAP          NaN   
51    686  20007            CAP          NaN   
52    686  20007            CAP          NaN   
53    687  20008            CAP            3   
54    688  20009            CAP            4   
55    689  20010            CAP          4.1   
56    690  20011            CAP          4.2   
57    691  20012            CAP          NaN   
58    692  20013            CAP          NaN   
59    693  20014            CAP          NaN   
60    695  20016            CAP          4.3   
61    696  20017            CAP          4.4   
62    698  20019            CAP          NaN   
63    699  20020            CAP          4.5   
64    700  20021            CAP          NaN   
65    701  20022            CAP          4.6   
66    702  20023            CAP          NaN   
67    703  20024            CAP          NaN   
68    704  20025            CAP          NaN   
69    705  20026            CAP          4.7   
70    706  20027            CAP          4.8   
71    707  20028            CAP          NaN   
72    708  20029            CAP          NaN   
73    709  20030            CAP          4.9   
74    711  20032            CAP            5   
75    712  20033            CAP          5.1   
76    713  20034            CAP          NaN   
77    714  20035            CAP          NaN   
78    715  20036            CAP          NaN   
79    716  20037            CAP          NaN   
80    717  20038            CAP          5.2   
81    718  20039            CAP          NaN   
82    719  20040    

2021-04-26 02:19:51,721 : XmlGeneration_Y : Initiating XML Generation
2021-04-26 02:19:51,721 : XmlGeneration_Y : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 02:19:51,911 : XmlGeneration_Y : Writing to File:Kalydeco II-86-PI-clean_SmPC.xml
2021-04-26 02:19:51,911 : XmlGeneration_Y : Writing to File:Kalydeco II-86-PI-clean_SmPC.xml


Created XML File For :- Kalydeco II-86-PI-clean_SmPC.json


### Annex II

In [326]:
documentNumber = 1
docFilter = "ANNEX II.json"
stopWordFilterLen = 6
stopWordlanguage = 'english'
start=0
end=1

In [327]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en
['Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json', 'Kalydeco II-86-PI-clean_ANNEX II.json', 'Kalydeco II-86-PI-clean_ANNEX III.json', 'Kalydeco II-86-PI-clean_SmPC.json']
['Kalydeco II-86-PI-clean_ANNEX II.json']
Starting Heading Extraction For File :- Kalydeco II-86-PI-clean_ANNEX II.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_ANNEX II.json
--------------------------------------------
AnnexII

OriginalCheck
('<=4|50.0|(50, 50, 100)|0.67|', 'Annex II', 'ANNEX II')

True  ||    ||  Annex II  ||  ANNEX II
True  ||  Contains<>|118.75|(61, 91, 86)|0.81|  ||  A.      MANUFACTURER(S) RESPONSIBLE FOR BATCH RELEASE   ||  A. <MANUFACTURER(S) OF THE BIOLOGICAL ACTIVE SUBSTANCE(S) AND> MANUFACTURER(S) RESPONSIBLE FOR BATCH RELEASE
True  ||    ||  B.      CONDITIONS OR RESTRICTIONS REGARDING SUPPLY AND USE  ||  B. CONDITIONS OR RESTRICTIO

2021-04-26 02:33:05,999 : ExtractContentBetween_K : Cleaning Match Results
2021-04-26 02:33:05,999 : ExtractContentBetween_K : Cleaning Match Results
2021-04-26 02:33:06,002 : ExtractContentBetween_K : Finished Cleaning Match Results
2021-04-26 02:33:06,002 : ExtractContentBetween_K : Finished Cleaning Match Results
2021-04-26 02:33:06,009 : ExtractContentBetween_K : Extracting Content Between Headings
2021-04-26 02:33:06,009 : ExtractContentBetween_K : Extracting Content Between Headings
2021-04-26 02:33:06,016 : ExtractContentBetween_K : Finished Extracting Content Between Headings
2021-04-26 02:33:06,016 : ExtractContentBetween_K : Finished Extracting Content Between Headings


True  ||    ||  ·         Obligation to conduct post-authorisation measures  ||  Obligation to conduct post-authorisation measures

OriginalCheck
('Contains<>|274.07|(8, 13, 86)|0.33|', 'The MAH shall complete, within the stated timeframe, the below measures:', 'E. SPECIFIC OBLIGATION TO COMPLETE POST-AUTHORISATION MEASURES FOR\r\n<THE CONDITIONAL MARKETING AUTHORISATION> <THE MARKETING AUTHORISATION UNDER EXCEPTIONAL CIRCUMSTANCES>')



Heading Not Found 
 ['Name and address of the manufacturer(s) of the biological active substance(s)', 'Official batch release', 'Additional risk minimisation measures', 'SPECIFIC OBLIGATION TO COMPLETE POST-AUTHORISATION MEASURES FOR\r\n<THE CONDITIONAL MARKETING AUTHORISATION> <THE MARKETING AUTHORISATION UNDER EXCEPTIONAL CIRCUMSTANCES>']


dict_keys([])
Completed Heading Extraction For File
Starting Document Annotation For File :- Kalydeco II-86-PI-clean_ANNEX II.json
Error Found
Completed Document Annotation For File
Starting Extracting Content Bet

index     id Procedure type Display code  \
0     740  21001            CAP          NaN   
1     741  21002            CAP            A   
2     744  21005            CAP            B   
3     746  21007            CAP            C   
4     748  21009            CAP            D   
5     741  21002            CAP            A   
6     743  21004            CAP          NaN   
7     744  21005            CAP            B   
8     746  21007            CAP            C   
9     747  21008            CAP          NaN   
10    748  21009            CAP            D   
11    749  21010            CAP          NaN   
12    751  21012            CAP          NaN   

                                                                                                         Name  \
0                                                                                                    ANNEX II   
1   <MANUFACTURER(S) OF THE BIOLOGICAL ACTIVE SUBSTANCE(S) AND> MANUFACTURER(S) RESPONSIBLE FOR BATCH RELEASE   
2                                                         CONDITIONS OR RESTRICTIONS REGARDING SUPPLY AND USE   
3                                            OTHER CONDITIONS AND REQUIREMENTS OF THE MARKETING AUTHORISATION   
4               CONDITIONS OR RESTRICTIONS WITH REGARD TO THE SAFE AND EFFECTIVE USE OF THE MEDICINAL PRODUCT   
5   <MANUFACTURER(S) OF THE BIOLOGICAL ACTIVE SUBSTANCE(S) AND> MANUFACTURER(S) RESPONSIBLE FOR BATCH RELEASE   
6                                       Name and address of the manufacturer(s) responsible for batch release   
7                                                         CONDITIONS OR RESTRICTIONS REGARDING SUPPLY AND USE   
8                                            OTHER CONDITIONS AND REQUIREMENTS OF THE MARKETING AUTHORISATION   
9                                                                      Periodic safety update reports (PSURs)   
10              CONDITIONS OR RESTRICTIONS WITH REGARD TO THE SAFE AND EFFECTIVE USE OF THE MEDICINAL PRODUCT   
11                                                                                 Risk management plan (RMP)   
12                                                          Obligation to conduct post-authorisation measures   

   parent_id  \
0        NaN   
1      21001   
2      21001   
3      21001   
4      21001   
5      21001   
6      21002   
7      21001   
8      21001   
9      21007   
10     21001   
11     21009   
12     21009   

                                                                                                 htmlText  \
0                                                                                                Annex II   
1                                                  A.      MANUFACTURER(S) RESPONSIBLE FOR BATCH RELEASE    
2                                             B.      CONDITIONS OR RESTRICTIONS REGARDING SUPPLY AND USE   
3                                C.      OTHER CONDITIONS AND REQUIREMENTS OF THE MARKETING AUTHORISATION   
4   D.      CONDITIONS OR RESTRICTIONS WITH REGARD TO THE SAFE AND EFFECTIVE USE OF THE MEDICINAL PRODUCT   
5                                                   A.      MANUFACTURER(S) RESPONSIBLE FOR BATCH RELEASE   
6                                   Name and address of the manufacturer(s) responsible for batch release   
7                                             B.      CONDITIONS OR RESTRICTIONS REGARDING SUPPLY AND USE   
8                                C.      Other conditions and requirements of the Marketing Authorisation   
9                                                        ·         Periodic safety update reports (PSURs)   
10  D.      Conditions or restrictions with regard to the safe and effective use of the medicinal product   
11                                                                   ·         Risk management plan (RMP)   
12                                            ·         Obligation to conduct post-authorisation measures 

2021-04-26 02:33:06,033 : XmlGeneration_e : Initiating XML Generation
2021-04-26 02:33:06,057 : XmlGeneration_e : Writing to File:Kalydeco II-86-PI-clean_ANNEX II.xml


Completed Extracting Content Between Heading
Created XML File For :- Kalydeco II-86-PI-clean_ANNEX II.json


### Labeling

In [328]:
documentNumber = 2
docFilter = "ANNEX III.json"
stopWordFilterLen = 6
stopWordlanguage = 'english'
start=0
end=1

In [329]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en
['Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json', 'Kalydeco II-86-PI-clean_ANNEX II.json', 'Kalydeco II-86-PI-clean_ANNEX III.json', 'Kalydeco II-86-PI-clean_SmPC.json']
['Kalydeco II-86-PI-clean_ANNEX III.json']
Starting Heading Extraction For File :- Kalydeco II-86-PI-clean_ANNEX III.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_ANNEX III.json
--------------------------------------------
Labelling
True  ||  <=1|25.0|(86, 100, 95)|0.92|  ||  A. LABELLING  ||  LABELLING 
True  ||  Contains<>|111.76|(64, 85, 86)|0.88|  ||  PARTICULARS TO APPEAR ON THE OUTER PACKAGING  ||  PARTICULARS TO APPEAR ON <THE OUTER PACKAGING> <AND> <THE IMMEDIATE PACKAGING>
True  ||    ||  1.         NAME OF THE MEDICINAL PRODUCT  ||  1. NAME OF THE MEDICINAL PRODUCT
True  ||    ||  2.         STATEMENT OF ACTIVE SUBSTANCE(S)  ||  2. STATEMENT OF ACTIVE

True  ||    ||  15.       INSTRUCTIONS ON USE  ||  15. INSTRUCTIONS ON USE
True  ||    ||  16.       INFORMATION IN BRAILLE  ||  16. INFORMATION IN BRAILLE
True  ||    ||  17.       UNIQUE IDENTIFIER – 2D BARCODE  ||  17. UNIQUE IDENTIFIER – 2D BARCODE
True  ||  <=7|2.33|(98, 98, 100)|0.99|  ||  18.       UNIQUE IDENTIFIER – HUMAN READABLE DATA  ||  18. UNIQUE IDENTIFIER - HUMAN READABLE DATA
True  ||    ||  MINIMUM PARTICULARS TO APPEAR ON BLISTERS OR STRIPS  ||  MINIMUM PARTICULARS TO APPEAR ON BLISTERS OR STRIPS
True  ||    ||  1.         NAME OF THE MEDICINAL PRODUCT  ||  1. NAME OF THE MEDICINAL PRODUCT

OriginalCheck
('<=7|26.32|(87, 87, 92)|0.87|', '2.         NAME OF THE MARKETING AUTHORISATION HOLDER', '11. NAME AND ADDRESS OF THE MARKETING AUTHORISATION HOLDER')

True  ||    ||  2.         NAME OF THE MARKETING AUTHORISATION HOLDER  ||  2. NAME OF THE MARKETING AUTHORISATION HOLDER
True  ||    ||  3.         EXPIRY DATE  ||  3. EXPIRY DATE
True  ||  Contains<>|173.33|(54, 100

True  ||    ||  15.       INSTRUCTIONS ON USE  ||  15. INSTRUCTIONS ON USE
True  ||    ||  16.       INFORMATION IN BRAILLE  ||  16. INFORMATION IN BRAILLE
True  ||    ||  17.       UNIQUE IDENTIFIER – 2D BARCODE  ||  17. UNIQUE IDENTIFIER – 2D BARCODE
True  ||  <=7|2.33|(98, 98, 100)|0.99|  ||  18.       UNIQUE IDENTIFIER – HUMAN READABLE DATA  ||  18. UNIQUE IDENTIFIER - HUMAN READABLE DATA
True  ||    ||  1.         NAME OF THE MEDICINAL PRODUCT  ||  1. NAME OF THE MEDICINAL PRODUCT
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  <=7|9.38|(96, 100, 97)|0.99|  ||  2.         STATEMENT OF ACTIVE SUBSTANCE  ||  2. STATEMENT OF ACTIVE SUBSTANCE(S)
True  ||    ||  3.         LIST OF EXCIPIENTS  ||  3. LIST OF EXCIPIENTS
True  ||    ||  4.         PHARMACEUTICAL FORM AND CONTENTS  ||  4. PHARMACEUTICAL FORM AND CONTENTS
True  ||    ||  5.         METHOD AND ROUTE(S) OF ADMINISTRATION  ||  5. METHOD AND ROUT

True  ||    ||  MINIMUM PARTICULARS TO APPEAR ON SMALL IMMEDIATE PACKAGING UNITS  ||  MINIMUM PARTICULARS TO APPEAR ON SMALL IMMEDIATE PACKAGING UNITS
True  ||    ||  1.       NAME OF THE MEDICINAL PRODUCT AND ROUTE(S) OF ADMINISTRATION  ||  1. NAME OF THE MEDICINAL PRODUCT AND ROUTE(S) OF ADMINISTRATION

OriginalCheck
('<=7|51.85|(78, 74, 91)|0.85|', '2.       METHOD OF ADMINISTRATION', '5. METHOD AND ROUTE(S) OF ADMINISTRATION')

True  ||    ||  2.       METHOD OF ADMINISTRATION  ||  2. METHOD OF ADMINISTRATION
True  ||    ||  3.       EXPIRY DATE  ||  3. EXPIRY DATE
True  ||  Contains<>|173.33|(54, 100, 90)|0.87|  ||  4.       BATCH NUMBER  ||  4. BATCH NUMBER<, DONATION AND PRODUCT CODES>
True  ||    ||  5.       CONTENTS BY WEIGHT, BY VOLUME OR BY UNIT  ||  5. CONTENTS BY WEIGHT, BY VOLUME OR BY UNIT
True  ||    ||  6.       OTHER  ||  6. OTHER
oooooooooooooooooooooooooooooooooooooooo END OF Sub Section oooooooooooooooooooooooooooooooooooooooooooooooooooooooooooo
True  ||  Contain

2021-04-26 02:34:42,462 : ExtractContentBetween_R : Cleaning Match Results
2021-04-26 02:34:42,467 : ExtractContentBetween_R : Finished Cleaning Match Results
2021-04-26 02:34:42,498 : ExtractContentBetween_R : Extracting Content Between Headings


...

index     id Procedure type Display code  \
0      753  22001            CAP          NaN   
1      754  22002            CAP          NaN   
2      755  22003            CAP            1   
3      756  22004            CAP            2   
4      757  22005            CAP            3   
5      758  22006            CAP            4   
6      759  22007            CAP            5   
7      760  22008            CAP            6   
8      761  22009            CAP            7   
9      762  22010            CAP            8   
10     763  22011            CAP            9   
11     764  22012            CAP           10   
12     765  22013            CAP           11   
13     766  22014            CAP           12   
14     767  22015            CAP           13   
15     768  22016            CAP           14   
16     769  22017            CAP           15   
17     770  22018            CAP           16   
18     771  22019            CAP           17   
19     772  22020            CAP           18   
20     773  22021            CAP          NaN   
21     774  22022            CAP            1   
22     775  22023            CAP            2   
23     776  22024            CAP            3   
24     777  22025            CAP            4   
25     778  22026            CAP            5   
26     754  22002            CAP          NaN   
27     755  22003            CAP            1   
28     756  22004            CAP            2   
29     757  22005            CAP            3   
30     758  22006            CAP            4   
31     759  22007            CAP            5   
32     760  22008            CAP            6   
33     761  22009            CAP            7   
34     762  22010            CAP            8   
35     763  22011            CAP            9   
36     764  22012            CAP           10   
37     765  22013            CAP           11   
38     766  22014            CAP           12   
39     767  22015            CAP           13   
40     768  22016            CAP           14   
41     769  22017            CAP           15   
42     770  22018            CAP           16   
43     771  22019            CAP           17   
44     772  22020            CAP           18   
45     754  22002            CAP          NaN   
46     755  22003            CAP            1   
47     756  22004            CAP            2   
48     757  22005            CAP            3   
49     758  22006            CAP            4   
50     759  22007            CAP            5   
51     760  22008            CAP            6   
52     761  22009            CAP            7   
53     762  22010            CAP            8   
54     763  22011            CAP            9   
55     764  22012            CAP           10   
56     765  22013            CAP           11   
57     766  22014            CAP           12   
58     767  22015            CAP           13   
59     768  22016            CAP           14   
60     769  22017            CAP           15   
61     770  22018            CAP           16   
62     771  22019            CAP           17   
63     772  22020            CAP           18   
64     773  22021            CAP          NaN   
65     774  22022            CAP            1   
66     775  22023            CAP            2   
67     776  22024            CAP            3   
68     777  22025            CAP            4   
69     778  22026            CAP            5   
70     754  22002            CAP          NaN   
71     755  22003            CAP            1   
72     756  22004            CAP            2   
73     757  22005            CAP            3   
74     758  22006            CAP            4   
75     759  22007            CAP            5   
76     760  22008            CAP            6   
77     761  22009            CAP            7   
78     762  22010            CAP            8   
79     763  22011            CAP            9   
80     764  22012            CAP    

2021-04-26 02:34:43,172 : XmlGeneration_O : Initiating XML Generation


Completed Extracting Content Between Heading


2021-04-26 02:34:43,435 : XmlGeneration_O : Writing to File:Kalydeco II-86-PI-clean_ANNEX III.xml


Created XML File For :- Kalydeco II-86-PI-clean_ANNEX III.json


### Package Leaflet

In [330]:
documentNumber = 3
docFilter = "LEAFLET.json"
stopWordFilterLen = 100
stopWordlanguage = 'english'
start=0
end=1
isPackageLeaflet = True

In [331]:
a,b,c = parseDocuments(procedureType,
               languageCode,
               documentNumber,
               docFilter,
               fileNameQrd,
               fileNameMatchRuleBook,
               fileNameDocumentTypeNames,
               stopWordFilterLen,
               start,
               end,
               isPackageLeaflet,
               "Kalydeco"
              )

F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en
['Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json', 'Kalydeco II-86-PI-clean_ANNEX II.json', 'Kalydeco II-86-PI-clean_ANNEX III.json', 'Kalydeco II-86-PI-clean_SmPC.json']
['Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json']
Starting Heading Extraction For File :- Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json
File being processed: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\partitionedJSONs\en\Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json
--------------------------------------------
Package leaflet
True  ||  <=4|16.67|(91, 100, 95)|0.91|  ||  B. PACKAGE LEAFLET  ||  PACKAGE LEAFLET
True  ||    ||  What is in this leaflet  ||  What is in this leaflet
----------------------------------
RemovedByStyle  ||    ||  1.   What Kalydeco is and what it is used for  ||  1. What Kalydeco is and what it is used for
----------------------------------
----------------------------------
RemovedByStyle  ||  Contains<

True  ||    ||  6.              Contents of the pack and other information  ||  6. Contents of the pack and other information
True  ||    ||  What Kalydeco contains  ||  What Kalydeco contains 
True  ||    ||  What Kalydeco looks like and contents of the pack  ||  What Kalydeco looks like and contents of the pack
True  ||  Contains<>|63.33|(76, 100, 90)|0.95|  ||  Marketing Authorisation Holder  ||  Marketing Authorisation Holder <and Manufacturer>
True  ||  SpecialCase1|84.38|(70, 100, 90)|0.94|  ||  This leaflet was last revised in   ||  This leaflet was last revised in <{MM/YYYY}><{month YYYY}>.
True  ||    ||  Other sources of information  ||  Other sources of information


2021-04-26 02:37:43,224 : ExtractContentBetween_C : Cleaning Match Results
2021-04-26 02:37:43,224 : ExtractContentBetween_C : Cleaning Match Results
2021-04-26 02:37:43,230 : ExtractContentBetween_C : Finished Cleaning Match Results
2021-04-26 02:37:43,230 : ExtractContentBetween_C : Finished Cleaning Match Results
2021-04-26 02:37:43,244 : ExtractContentBetween_C : Extracting Content Between Headings
2021-04-26 02:37:43,244 : ExtractContentBetween_C : Extracting Content Between Headings
2021-04-26 02:37:43,258 : ExtractContentBetween_C : Finished Extracting Content Between Headings
2021-04-26 02:37:43,258 : ExtractContentBetween_C : Finished Extracting Content Between Headings




Heading Not Found 
 ['q This medicine is subject to additional monitoring. This will allow quick identification of new safety information. You can help by reporting any side effects you may get. See the end of section 4 for how to report side effects.', 'Do not <take> <use> X', 'X contains {name the excipient(s)}', 'For any information about this medicine, please contact the local representative of the Marketing Authorisation Holder:', 'The following information is intended for healthcare professionals only:']


dict_keys(['1. What Kalydeco is and what it is used for', '2. What you need to know before you <take> <use> Kalydeco ', '3. How to <take> <use> Kalydeco ', '4. Possible side effects', '5. How to store Kalydeco', '6. Contents of the pack and other information', 'Kalydeco contains {name the excipient(s)}'])
Completed Heading Extraction For File
Starting Document Annotation For File :- Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json
Error Found
Completed Document Annotation For Fi

index     id Procedure type Display code  \
0     786  23001            CAP          NaN   
1     788  23003            CAP          NaN   
2     789  23004            CAP            1   
3     790  23005            CAP            2   
4     792  23007            CAP          NaN   
5     793  23008            CAP          NaN   
6     794  23009            CAP          NaN   
7     795  23010            CAP          NaN   
8     796  23011            CAP          NaN   
9     797  23012            CAP          NaN   
10    799  23014            CAP            3   
11    800  23015            CAP          NaN   
12    801  23016            CAP          NaN   
13    802  23017            CAP          NaN   
14    803  23018            CAP          NaN   
15    804  23019            CAP            4   
16    805  23020            CAP          NaN   
17    806  23021            CAP          NaN   
18    807  23022            CAP            5   
19    808  23023            CAP            6   
20    809  23024            CAP          NaN   
21    810  23025            CAP          NaN   
22    811  23026            CAP          NaN   
23    813  23028            CAP          NaN   
24    814  23029            CAP          NaN   
25    788  23003            CAP          NaN   
26    789  23004            CAP            1   
27    790  23005            CAP            2   
28    792  23007            CAP          NaN   
29    794  23009            CAP          NaN   
30    795  23010            CAP          NaN   
31    797  23012            CAP          NaN   
32    799  23014            CAP            3   
33    801  23016            CAP          NaN   
34    804  23019            CAP            4   
35    805  23020            CAP          NaN   
36    806  23021            CAP          NaN   
37    807  23022            CAP            5   
38    808  23023            CAP            6   
39    809  23024            CAP          NaN   
40    810  23025            CAP          NaN   
41    811  23026            CAP          NaN   
42    813  23028            CAP          NaN   
43    814  23029            CAP          NaN   

                                                           Name parent_id  \
0                                               PACKAGE LEAFLET       NaN   
1                                       What is in this leaflet     23001   
2                             What X is and what it is used for     23001   
3              What you need to know before you <take> <use> X      23001   
4                                     Warnings and precautions      23005   
5                                    Children <and adolescents>     23005   
6                                         Other medicines and X     23005   
7               X with <food> <and> <,> <drink> <and> <alcohol>     23005   
8            Pregnancy <and> <,> breast-feeding <and fertility>     23005   
9                                    Driving and using machines     23005   
10                                       How to <take> <use> X      23001   
11                            Use in children <and adolescents>     23014   
12                   If you <take> <use> more X than you should     23014   
13                             If you forget to <take> <use> X>     23014   
14                              If you stop <taking> <using> X>     23014   
15                                        Possible side effects     23001   
16        Additional side effects in children <and adolescents>     23019   
17                                    Reporting of side effects     23019   
18                                               How to store X     23001   
19                   Contents of the pack and other information     23001   
20                                             What X contains      23023   
21                   What X looks like and contents of the pack     23023   
22            Marketing Authorisation Holder <and Manufacturer>     2302

2021-04-26 02:37:43,300 : XmlGeneration_d : Initiating XML Generation
2021-04-26 02:37:43,404 : XmlGeneration_d : Writing to File:Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.xml


Completed Extracting Content Between Heading
Created XML File For :- Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json


In [288]:
from match.rulebook.matchRulebook import MatchRuleBook

rules= MatchRuleBook(
            fileNameRuleBook= fileNameMatchRuleBook,
            procedureType= procedureType,
            languageCode= languageCode,
            documentNumber= 0).ruleDict



In [289]:
from match.matchStrings.matchStrings import MatchStrings

In [290]:
matchString = MatchStrings(0, rules, 6, 'german')


In [291]:
o,t = '6.5     Art und Inhalt des Behältnisses', '6.5 Art und Inhalt des Behältnisses <und spezielles Zubehör für den Gebrauch, die Anwendung oder die Implantation>'

#o = o.encode()
#print(o.decode())
matchString.matchStrings(o,t,52)

(False, 'SpecialCase1|180.0|(45, 77, 86)|0.67|')

In [337]:
fileNameDoc

NameError: name 'fileNameDoc' is not defined

In [353]:
from utils.logger.matchLogger import MatchLogger

In [354]:
 os.path.join(os.path.abspath(os.path.join('..')), 'code','utils','matchLog.txt')

'F:\\Projects\\EMA\\Repository\\EMA EPI PoC\\function_code\\code\\utils\\matchLog.txt'

In [355]:
m = MatchLogger("MatchLogger",'Kalydeco II-86-PI-clean_ PACKAGE LEAFLET.json', 'CAP', 'en', 'SmPC', fileNameLog = os.path.join(os.path.abspath(os.path.join('..')), 'code','utils','matchLog.txt'))

In [356]:
extra = {"custom_dimensions": m.customDimension}

In [357]:
m.logger.info("Match Found:",extra=extra)


2021-04-26 03:26:25,972 : MatchLogger : Match Found:
2021-04-26 03:26:25,972 : MatchLogger : Match Found:
2021-04-26 03:26:25,972 : MatchLogger : Match Found:
2021-04-26 03:26:25,972 : MatchLogger : Match Found:
